# Title
[]()

In [2]:
from pandas import json_normalize  
import pandas as pd
import sys
sys.path.append(r"C:\Users\silvh\OneDrive\lighthouse\custom_python")
sys.path.append(r"C:\Users\silvh\OneDrive\lighthouse\portfolio-projects\online-PT-social-media-NLP\src")
from silvhua import *
from datetime import datetime
# import json
# from plotly.subplots import make_subplots
# import requests

In [3]:
# set the option to wrap text within cells
# pd.reset_option('all')
# pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_colwidth', 300)
# pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)

In [4]:
# from pypdf import PdfReader
import pandas as pd
import openai
import os
# from openai.embeddings_utils import get_embedding, cosine_similarity
import re

In [5]:

sys.path.append(r"C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\src")
from summarization import Chatbot, reply, batch_reply
from article_processing import create_text_dict

# Create text_dict

In [6]:
import os

folder_path = '../text/2023-04-17'
encoding='ISO-8859-1'
all_files = []

for filename in os.listdir(folder_path):
    with open(os.path.join(folder_path, filename), 'r', encoding=encoding) as f:
        all_files.append(f.read())

text_dict = create_text_dict(all_files)
text_dict

{1: 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health\n\nTHE EFFICACY OF EXERCISE SNACKS FOR IMPROVING CRF IN INACTIVE ADULTS\n\nOur first exercise snacks study (15) was developed based on previous work showing a ~1 MET improvement in CRF after a 6-wk stair climbing protocol that involved 3 × 20-s hard efforts over a 10-min period performed 3 d·wk?1 (26). In the subsequent study (15), we exposed previously inactive young adults to an intervention involving either three daily bouts of vigorous stair climbing performed 1\x964 h apart on 3 d·wk?1 or a no-exercise control (n = 12 per group) (15). For each stair-based exercise snack, participants were instructed to safely ascend 60 steps in a three-flight stairwell as quickly as possible. Each exercise snack was preceded by a dynamic warm-up (10 jumping jacks, 10 air squats, and 5 lunges on each side) and followed by a 1-min walking cooldown. After the 6-wk intervention, there were modest, albeit significant, improvements 

## Create relevance_prompts_df

In [7]:
from itertools import product
prompts_dict = dict()
experiment_num = 1
relevance_prompts_dict = dict()

prep_step = [
    # "Take the key points to",
    "Take the key points and numerical descriptors to",
    # ""
]

task_part1 = [
    # "Summarize the article in under 300 characters",
    "Summarize for a LinkedIn post",
    # "Summarize for a tweet",
    # "Summarize in an engaging way",
    "Describe the interesting points to your coworker at the water cooler"
    # "Summarize the article for a Tiktok post"
]
audience = [
    # "lay audience",
    # "",
    "seniors",
    "people who enjoy sports"
]
task_part2 = [
    # "",
    # "Use terms a 12-year-old can understand.",
    "Assume your audience has no science background.",
    "Make the language appropriate for a lay audience"
    # "Include the most interesting findings.",
    # "Include the key take-aways for the reader.",
    # "Include the implications of the article."
]

task_part3 =[
    "Add 1-2 sentences to make this relevant for"
    # "Add 1-2 sentences to make this relevant for older adults."
    # "Once you are done, add 1-2 sentences to make this relevant for older adults.",
    ""
]

# prompts_df = pd.DataFrame(product(prep_step, task_part1, task_part2, task_part3, audience), 
#     columns=['prep_step', 'task part 1', 'task part 2', 'task part 3', 'audience'])

summarize_task = pd.DataFrame(product(prep_step, task_part1), 
    columns=['prep_step', 'task part 1'])

relevance_prompts_df = pd.DataFrame(product(task_part3, audience), 
    columns=['task part 3', 'audience'])



# prompts_df['prompt'] = prompts_df.apply(
#     lambda row: f"{row['prep_step']} {row['task part 1']}.", 
#     axis=1)
# prompts_df['simplify'] = prompts_df.apply(
#     lambda row: f" {row['task part 2'] if row['task part 2'] else ''}", 
#     axis=1)
relevance_prompts_df['relevance'] = relevance_prompts_df.apply(
    lambda row: f" {row['task part 3']} {row['audience']} " if row['audience'] else '', 
    axis=1) 
relevance_prompts_dict[experiment_num] = relevance_prompts_df
relevance_prompts_df

task part 3                 audience  \
0  Add 1-2 sentences to make this relevant for                  seniors   
1  Add 1-2 sentences to make this relevant for  people who enjoy sports   

                                                               relevance  
0                   Add 1-2 sentences to make this relevant for seniors   
1   Add 1-2 sentences to make this relevant for people who enjoy sports

# Most updated Class script
* batch_summarize_chain produces output to facilitate future ML. Need to update simplify and add_relevance methods to do the same.

In [ ]:

import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                # self.qna[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna['summary'] = [value for value in self.summaries_dict.values()]
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.simplify_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                response = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.simple_summary_dict['simplify_task'] = simplify_task
        # self.qna = {**self.qna, **self.simple_summary_dict}
        self.qna['simple summaries'] = [{key: value} for key, value in self.simple_summary_dict.items()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.simple_summary_dict
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        # self.qna = {**self.qna, **self.relevance_dict}
        self.qna['added relevance'] = [{key: value} for key, value in self.simple_summary_dict.items()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.relevance_dict

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict
    # return qna_dfs_list, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    for column, text_prompt_key in enumerate(chaining_bot_dict):
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            simple_summaries_df[column] = pd.concat([
                pd.DataFrame(value, name=key) for key, value in simple_summaries_master_dict[text_prompt_key].items()
            ])   
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    try:
        qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        temp_qna_chain_dict = pd.concat([
            qna_chain_dict[summary_iteration_id], 
            simple_summaries_df
            ])
        qna_chain_dict[iteration_id] = temp_qna_chain_dict
        print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
        if save_outputs:
            try:
                save_output(
                    qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to concatenate simple summary DataFrame to original DataFrame')
        qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict

    return qna_chain_dict




# Iteration 1

In [2]:
dict = {'a': [1, 2, 3]}
dict.setdefault('a', [])
dict['a'].extend([4, 5])
dict

{'a': [1, 2, 3, 4, 5]}

In [3]:
dict2 = {'a': [1, 2, 3]}
dict2.setdefault('b', [])
dict2['b'].extend([4, 5])
dict2

{'a': [1, 2, 3], 'b': [4, 5]}

In [ ]:
dict3 = {'a': [1, 2, 3]}
dict3.setdefault('b', [])
dict3['b'].extend([4, 5])
dict3

In [13]:

import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.set_default('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except:
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.simplify_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                response = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault('simple summaries', [])
        self.qna['simple summaries'].extend([value for value in self.simple_summary_dict.values()])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.simple_summary_dict
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.relevance_dict

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    for column, text_prompt_key in enumerate(chaining_bot_dict):
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            simple_summaries_df[column] = pd.concat([
                pd.DataFrame(value, name=key) for key, value in simple_summaries_master_dict[text_prompt_key].items()
            ])   
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    try:
        qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        temp_qna_chain_dict = pd.concat([
            qna_chain_dict[summary_iteration_id], 
            simple_summaries_df
            ])
        qna_chain_dict[iteration_id] = temp_qna_chain_dict
        print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
        if save_outputs:
            try:
                save_output(
                    qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to concatenate simple summary DataFrame to original DataFrame')
        qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict

    return qna_chain_dict


iteration_id = 1
n_choices = 2
qna_dict = dict()
chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 2
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=1,
    iteration_id=iteration_id)


**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	**Error with response parsing**
	...Success!
[batch_summarize()] Sleeping 1 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	**Error with response parsing**
	...Success!
[batch_summarize()] Sleeping 1 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	**Error with response parsing**
	...Success!
[batch_summarize()] Sleeping 1 sec to avoid exceeding API rate limit
**Text #2 pro

### reference: qna_dict

In [14]:
qna_dict[iteration_id]

[{0: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
   'system_role': 'You are an expert at science communication.',
   'model': 'gpt-3.5-turbo',
   'prep step': 'Take the key points and numerical descriptors to',
   'summarization task': 'Summarize for a LinkedIn post'},
  1: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
   'system_role': 'You are an expert at science communication.',
   'model': 'gpt-3.5-turbo',
   'prep step': 'Take the key points and numerical descriptors to',
   'summarization task': 'Describe the interesting points to your coworker at the water cooler'}},
 {0: {'article_title': 'Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory',
   'system_role': 'You are an expert at science communication.',
   'model': 'gpt-3.5-turbo',
   'prep step': 'Take the key points and numerical descriptors to',
   'summarization task': 'Summarize for

## 1.1

In [17]:

import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.simplify_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            simplify_prompt = self.simplify_bot_dict[new_key].create_prompt(simplify_task)
            try:
                response = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault('simple summaries', [])
        self.qna['simple summaries'].extend([value for value in self.simple_summary_dict.values()])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.simple_summary_dict
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.relevance_dict

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    for column, text_prompt_key in enumerate(chaining_bot_dict):
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            simple_summaries_df[column] = pd.concat([
                pd.DataFrame(value, name=key) for key, value in simple_summaries_master_dict[text_prompt_key].items()
            ])   
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    try:
        qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        temp_qna_chain_dict = pd.concat([
            qna_chain_dict[summary_iteration_id], 
            simple_summaries_df
            ])
        qna_chain_dict[iteration_id] = temp_qna_chain_dict
        print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
        if save_outputs:
            try:
                save_output(
                    qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to concatenate simple summary DataFrame to original DataFrame')
        qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict

    return qna_chain_dict


iteration_id = 1.1
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 2
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=1,
    iteration_id=iteration_id)


**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 1 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 1 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 1 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating promp

In [18]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to simultaneously improve cardiometabolic health and reduce the impact of sedentariness on the general population. Emerging evidence suggests that exerc...   
2  Exercise snacks, defined as short bouts of vigorous exercise performed multiple times throughout the day, are a feasible and effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving cycling or stair climbing can improve cardiorespiratory fitness and...   
1  Hey, have you heard about this new exercise strategy called "exercise snacks"? It's a novel approach to improving cardiometabolic health by performing isolated bouts of brief vigorous exercise multiple times throughout the day. Studies have shown that exercise snacks involving thrice daily ~15-3...   
2  Hey there! Have you heard of exercise snacks? It's a new strategy that involves performing isolated bouts of 

In [19]:
simplify_prompts

['Assume your audience has no science background.',
 'Make the language appropriate for a lay audience']

In [20]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 1.1
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01


TypeError: __init__() got an unexpected keyword argument 'n_choices'

In [21]:
chaining_dict[iteration_id]

{'text1_prompt00': <__main__.Chaining at 0x1543b959670>,
 'text1_prompt01': <__main__.Chaining at 0x1543b2af250>,
 'text2_prompt00': <__main__.Chaining at 0x1541a7a7430>,
 'text2_prompt01': <__main__.Chaining at 0x1543b2af1f0>}

## 1.2

In [27]:

import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            # self.simplify_bot_dict[new_key] = Chaining(
            #     summary, system_role=system_role,
            #     model=model, temperature=temperature, max_tokens=max_tokens
            #     )
            simplify_prompt = self.create_prompt(simplify_task)
            self.qna.setdefaultkey('simplify task', [])
            self.qna['simplify task'].extend(simplify_prompt)
            try:
                response = self.gpt(simplify_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault('simple summaries', [])
        self.qna['simple summaries'].extend([value for value in self.simple_summary_dict.values()])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.simple_summary_dict
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.relevance_dict

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        # simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_list.append(summary_dict)


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        # try:
        #     simple_summaries_df[column] = pd.concat([
        #         pd.DataFrame(value, name=key) for key, value in simple_summaries_master_dict[text_prompt_key].items()
        #     ])   
        # except Exception as error:
        #     exc_type, exc_obj, tb = sys.exc_info()
        #     f = tb.tb_frame
        #     lineno = tb.tb_lineno
        #     filename = f.f_code.co_filename
        #     print("An error occurred on line", lineno, "in", filename, ":", error)
        #     print('Unable to create results DataFrame')
            
        #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 1.2
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

# summary_iteration_id = iteration_id
# summary_iteration_id = 1.1
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=1,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 1 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 1 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 1 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating promp

In [28]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks are short bouts of vigorous exercise performed multiple times throughout the day. This strategy has been shown to be efficacious for improving cardiorespiratory fitness and exercise performance in inactive adults. It may also have potential to improve aspects of cardiometabolic h...   
2  Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, are a novel strategy to improve cardiometabolic health. Studies suggest that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling and more practical stair climbin...   
1  Hey! Have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health. Basically, it involves performing isolated bouts of brief vigorous exercise multiple times throughout the day. And guess what? It's been shown to be effective in improving cardiorespiratory fitness ...   
2  Hey, have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health! Basically, 

In [30]:
summary_iteration_id = iteration_id
# summary_iteration_id = 1.1
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 1.2
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt


AttributeError: 'dict' object has no attribute 'setdefaultkey'

## 1.3

In [32]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            # self.simplify_bot_dict[new_key] = Chaining(
            #     summary, system_role=system_role,
            #     model=model, temperature=temperature, max_tokens=max_tokens
            #     )
            simplify_prompt = self.create_prompt(simplify_task)
            self.qna.setdefault('simplify task', [])
            self.qna['simplify task'].extend(simplify_prompt)
            try:
                response = self.gpt(simplify_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault('simple summaries', [])
        self.qna['simple summaries'].extend([value for value in self.simple_summary_dict.values()])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.simple_summary_dict
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.relevance_dict

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        # simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_list.append(summary_dict)


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        # try:
        #     simple_summaries_df[column] = pd.concat([
        #         pd.DataFrame(value, name=key) for key, value in simple_summaries_master_dict[text_prompt_key].items()
        #     ])   
        # except Exception as error:
        #     exc_type, exc_obj, tb = sys.exc_info()
        #     f = tb.tb_frame
        #     lineno = tb.tb_lineno
        #     filename = f.f_code.co_filename
        #     print("An error occurred on line", lineno, "in", filename, ":", error)
        #     print('Unable to create results DataFrame')
            
        #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 1.3
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

# summary_iteration_id = iteration_id
# summary_iteration_id = 1.1
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [33]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy for improving cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling a...   
2  Exercise snacks, defined as brief and isolated bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Several studies have shown that exercise snacks, such as stair climbing or cycling, can improve cardiorespiratory...   
1  Hey! Have you heard about exercise snacks? They're brief, isolated bouts of vigorous exercise performed multiple times throughout the day. And according to recent studies, they may be an effective strategy for improving cardiometabolic health in previously inactive adults. The studies involved e...   
2  Hey there! Have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health. Basic

In [34]:
summary_iteration_id = iteration_id
# summary_iteration_id = 1.1
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 1.3
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
An error occurred on line 125 in C:\Users\silvh\AppData\Local\Temp\ipykernel_26688\2880937760.py : gpt() missing 1 required positional argument: 'n_choices'
	**API request failed for `.simplify()`**
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
An error occurred on line 125 in C:\Users\silvh\AppData\Local\Temp\ipykernel_26688\2880937760.py : gpt() missing 1 required positional argument: 'n_choices'
	**API request failed for `.simplify()`**
**text1_prompt01
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
An error occurred on line 125 in C:\Users\silvh\AppData\Local\Temp\ipykernel_26688\2880937760.py : gpt() missing 1 required

## 1.4

In [35]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            # self.simplify_bot_dict[new_key] = Chaining(
            #     summary, system_role=system_role,
            #     model=model, temperature=temperature, max_tokens=max_tokens
            #     )
            simplify_prompt = self.create_prompt(simplify_task)
            self.qna.setdefault('simplify task', [])
            self.qna['simplify task'].extend(simplify_prompt)
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault('simple summaries', [])
        self.qna['simple summaries'].extend([value for value in self.simple_summary_dict.values()])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.simple_summary_dict
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.relevance_dict

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        # simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_list.append(summary_dict)


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        # try:
        #     simple_summaries_df[column] = pd.concat([
        #         pd.DataFrame(value, name=key) for key, value in simple_summaries_master_dict[text_prompt_key].items()
        #     ])   
        # except Exception as error:
        #     exc_type, exc_obj, tb = sys.exc_info()
        #     f = tb.tb_frame
        #     lineno = tb.tb_lineno
        #     filename = f.f_code.co_filename
        #     print("An error occurred on line", lineno, "in", filename, ":", error)
        #     print('Unable to create results DataFrame')
            
        #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 1.4
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

# summary_iteration_id = iteration_id
# summary_iteration_id = 1.1
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [36]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling and ...   
2  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve CRF and reduce the impact of sedentariness on cardiometabolic health. The emerging evidence from various studies suggests that exercise snack...   
1  Hey, have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health by performing isolated bouts of brief vigorous exercise multiple times throughout the day. Studies have shown that exercise snacks involving cycling or stair climbing can improve cardiorespiratory fi...   
2  Hey! Have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health by performin

In [37]:
summary_iteration_id = iteration_id
# summary_iteration_id = 1.1
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 1.4
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [39]:
pd.DataFrame(qna_dict[iteration_id])

simple_summary01_prompt0_option01  \
0  Exercise snacks are a new strategy to improve our health. These snacks are short bursts of exercise, lasting only a few seconds, that are done multiple times throughout the day. This type of exercise has been shown to improve our cardiovascular fitness and exercise performance, even in people wh...   
1                                                                                                                                                                                                                                                                                                          NaN   
2  Exercise snacks are short bouts of vigorous exercise that can be performed multiple times throughout the day. They have been shown to improve cardiorespiratory fitness and exercise performance in inactive adults. In addition, exercise snacks may have potential to improve aspects of cardiometabol...   
3                                                                                                                                                                                                                                                                                                          NaN   
4  This article talks about a study that looked at how seeing pictures of yummy foods and feeling stressed affects how much people snack on those foods. The study found that both seeing yummy food pictures and feeling stressed made people want to eat more of those foods. The study also found that h...   
5                                                                                                                                                                                                                                                                                                          NaN   
6  This study looked at how seeing pictures of delicious food and feeling stressed affects how much people snack on tasty but unhealthy foods. The researchers found that both food pictures and stress made people crave and eat more of these foods, especially if they were already overweight. The stud...   
7                                                                                                                                                                                                                                                                                                          NaN   

                                                                                                                                                                                                                                                                             simple_summary01_prompt0_option02  \
0  Exercise Snacks are short bursts of exercise that can be performed multiple times throughout the day. They have been shown to be effective in improving cardiovascular fitness and exercise performance in inactive adults. The exercise snacks involve a 15-30 second burst of vigorous exercise, eithe...   
1                                                                                                                                                                                                                                                                                                          NaN   
2  Exercise snacks are short bouts of vigorous exercise that can be performed multiple times throughout the day. They have been shown to improve cardiorespiratory fitness and exercise performance in inactive adults. Exercise snacks involve brief periods of hard effort, such as climbing stairs or cy...   
3                                                                                                                                                                                                                                                                                                 

In [38]:
qna_dict[iteration_id]

[{'simple_summary01_prompt0_option01': "Exercise snacks are a new strategy to improve our health. These snacks are short bursts of exercise, lasting only a few seconds, that are done multiple times throughout the day. This type of exercise has been shown to improve our cardiovascular fitness and exercise performance, even in people who were previously inactive. The exercise snacks involve either cycling or stair climbing and can be done at home, work, or school. They are not too intense, and you won't need any special equipment. These exercise snacks are a great way to combat the health problems associated with sedentary lifestyles.",
  'simple_summary01_prompt0_option02': 'Exercise Snacks are short bursts of exercise that can be performed multiple times throughout the day. They have been shown to be effective in improving cardiovascular fitness and exercise performance in inactive adults. The exercise snacks involve a 15-30 second burst of vigorous exercise, either cycling or stair cl

## 1.5

In [40]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            # self.simplify_bot_dict[new_key] = Chaining(
            #     summary, system_role=system_role,
            #     model=model, temperature=temperature, max_tokens=max_tokens
            #     )
            simplify_prompt = self.create_prompt(simplify_task)
            self.qna.setdefault('simplify task', [])
            self.qna['simplify task'].extend(simplify_prompt)
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault('simple summaries', [])
        self.qna['simple summaries'].extend([value for value in self.simple_summary_dict.values()])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.simple_summary_dict
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.relevance_dict

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        # try:
        #     simple_summaries_df[column] = pd.concat([
        #         pd.DataFrame(value, name=key) for key, value in simple_summaries_master_dict[text_prompt_key].items()
        #     ])   
        # except Exception as error:
        #     exc_type, exc_obj, tb = sys.exc_info()
        #     f = tb.tb_frame
        #     lineno = tb.tb_lineno
        #     filename = f.f_code.co_filename
        #     print("An error occurred on line", lineno, "in", filename, ":", error)
        #     print('Unable to create results DataFrame')
            
        #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 1.5
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

# summary_iteration_id = iteration_id
summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

# qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
#     n_choices=n_choices, pause_per_request=pause_per_request,
#     iteration_id=iteration_id)

qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 1.4
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [50]:
qna_dict[iteration_id]

[{0: {'simple_summary01_prompt0_option01': 'Exercise snacks are a new approach to improving health that involves doing short bursts of exercise throughout the day, rather than one long workout. Studies have shown that even brief, intense exercise can improve cardiovascular fitness and other markers of health. These exercise snacks can be done using stairs or cycling, and can be easily incorporated into daily life. Breaking up long periods of sitting with exercise snacks has also been shown to improve insulin levels and blood flow, which are important for overall health. Exercise snacks align with new guidelines that encourage short bouts of physical activity throughout the day, and can be a practical and effective way to improve health for people who are not currently active.',
   'simple_summary01_prompt0_option02': 'Exercise snacks are a new strategy that can improve your health, specifically your heart and metabolism. Inactive adults were studied to see if short bursts of exercise, 

In [49]:
pd.concat([pd.DataFrame(data, index=[0, 1]) for dictionary in qna_dict[iteration_id] for data in dictionary.values()])

simple_summary01_prompt0_option01  \
0  Exercise snacks are a new approach to improving health that involves doing short bursts of exercise throughout the day, rather than one long workout. Studies have shown that even brief, intense exercise can improve cardiovascular fitness and other markers of health. These exercise snacks can be ...   
1  Exercise snacks are a new approach to improving health that involves doing short bursts of exercise throughout the day, rather than one long workout. Studies have shown that even brief, intense exercise can improve cardiovascular fitness and other markers of health. These exercise snacks can be ...   
0                                                                                                                                                                                                                                                                                                          NaN   
1                                                                                                                                                                                                                                                                                                          NaN   
0  Exercise snacks are short bursts of vigorous exercise that can be done multiple times throughout the day. These snacks involve brief periods of hard effort, such as climbing stairs or cycling, and can be done in a practical setting like at home or in the office. Recent studies have shown that ex...   
1  Exercise snacks are short bursts of vigorous exercise that can be done multiple times throughout the day. These snacks involve brief periods of hard effort, such as climbing stairs or cycling, and can be done in a practical setting like at home or in the office. Recent studies have shown that ex...   
0                                                                                                                                                                                                                                                                                                          NaN   
1                                                                                                                                                                                                                                                                                                          NaN   
0  This study looked at how seeing pictures of yummy food and feeling stressed affects our desire to eat unhealthy snacks. The researchers found that both food pictures and stress made people want to eat more unhealthy snacks, especially if they were already overweight. They also found that certain...   
1  This study looked at how seeing pictures of yummy food and feeling stressed affects our desire to eat unhealthy snacks. The researchers found that both food pictures and stress made people want to eat more unhealthy snacks, especially if they were already overweight. They also found that certain...   
0                                                                                                                                                                                                                                                                                                          NaN   
1                                                                                                                                                                                                                                                                                                          NaN   
0  This study looked at how seeing pictures of yummy food and feeling stressed affects how much people eat. The researchers found that when people saw pictures of delicious snacks or felt stressed, they wanted to eat more of those snacks. This was especially true for people who were overwei

## 1.6

In [54]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            # self.simplify_bot_dict[new_key] = Chaining(
            #     summary, system_role=system_role,
            #     model=model, temperature=temperature, max_tokens=max_tokens
            #     )
            simplify_prompt = self.create_prompt(simplify_task)
            self.qna.setdefault('simplify task', [])
            self.qna['simplify task'].extend(simplify_prompt)
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault('simple summary', [])
        self.qna['simple summary'].extend([value for value in self.simple_summary_dict.values()])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            qna_dict[iteration_id] = pd.concat([
                pd.DataFrame(
                    data, index=[choice for choice in range(1, len(data['simple summary'])+1)]
                ) for dictionary in simple_summaries_master_list for data in dictionary.values()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 1.6
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

### Results: summary

In [55]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Studies have shown that exercise snacks can improve cardiorespiratory fitness and exercise performance in sedentary adults. Addi...   
2  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health in previously inactive adults. Recent studies have demonstrated that exercise snacks involving thrice daily ~15-30 sec...   
1  Hey, did you know that there's a new exercise strategy called "exercise snacks" that can improve cardiometabolic health? It involves isolated bouts of brief, vigorous exercise performed multiple times throughout the day. The research shows that it is efficacious for improving cardiorespiratory f...   
2  Hey there! Have you heard of exercise snacks? It's a new strategy to improve cardiometabolic health! Essentia

In [56]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 1.6
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [57]:
qna_dict[iteration_id]

[{0: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
   'system_role': 'You are an expert at science communication.',
   'model': 'gpt-3.5-turbo',
   'prep step': 'Take the key points and numerical descriptors to',
   'summarization task': 'Summarize for a LinkedIn post',
   'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Studies have shown that exercise snacks can improve cardiorespiratory fitness and exercise performance in sedentary adults. Additionally, breaking up prolonged periods of sitting with hourly bouts of vigorous exercise snacks has been shown to reduce insulin levels and nonesterified fatty acids in individuals with overweight/obesity. Exercise snacks align with the recently revised Physical Activity Guidelines for Americans and the World Health Organization Guidelines on Physical Activity and Sedenta

In [61]:
qna_dict[iteration_id][0]

{0: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Studies have shown that exercise snacks can improve cardiorespiratory fitness and exercise performance in sedentary adults. Additionally, breaking up prolonged periods of sitting with hourly bouts of vigorous exercise snacks has been shown to reduce insulin levels and nonesterified fatty acids in individuals with overweight/obesity. Exercise snacks align with the recently revised Physical Activity Guidelines for Americans and the World Health Organization Guidelines on Physical Activity and Sedentary Beh

In [60]:
pd.DataFrame(qna_dict[iteration_id][0])

0  \
article_title                                                                                                                                                                                                                                                Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
system_role                                                                                                                                                                                                                                                                         You are an expert at science communication.   
model                                                                                                                                                                                                                                                                                                             gpt-3.5-turbo   
prep step                                                                                                                                                                                                                                                                      Take the key points and numerical descriptors to   
summarization task                                                                                                                                                                                                                                                                                Summarize for a LinkedIn post   
summary             [Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Studies have shown that exercise snacks can improve cardiorespiratory fitness and exercise performance in sedentary adults. Add...   
simplify task       [{'role': 'system', 'content': 'You are an expert at science communication.'}, {'role': 'user', 'content': 'Given the following text: Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health

THE EFFICACY OF EXERCISE SNACKS FOR IMPROVING CRF IN INACTIVE ADULTS

Our first exercise snack...   
simple summary      [Exercise snacks are short bursts of intense exercise that can be performed throughout the day. They are a new strategy to improve heart and metabolic health. Studies have shown that exercise snacks can improve cardiovascular fitness in previously inactive young adults. The exercise snacks invol...   
text                Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health\n\nTHE EFFICACY OF EXERCISE SNACKS FOR IMPROVING CRF IN INACTIVE ADULTS\n\nOur first exercise snacks study (15) was developed based on previous work showing a ~1 MET improvement in CRF after a 6-wk stair climbing protocol that in...   

                                                                                                                                                                                                                                                                                                                              1  
article_title                                                                                                                                                                                                                                                Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health  
system_role                                                                                                                                                                                                                                                                         You are an expert at science communication.  
model                                                                                                                    

In [58]:
pd.concat([pd.DataFrame(data) for dictionary in qna_dict[iteration_id] for data in dictionary.values()])

ValueError: All arrays must be of the same length

## 1.7

In [65]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            # self.simplify_bot_dict[new_key] = Chaining(
            #     summary, system_role=system_role,
            #     model=model, temperature=temperature, max_tokens=max_tokens
            #     )
            simplify_prompt = self.create_prompt(simplify_task)
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)
            self.qna[f'simplify task {key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault('simple summary', [])
        self.qna['simple summary'].extend([value for value in self.simple_summary_dict.values()])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            qna_dict[iteration_id] = pd.concat([
                pd.DataFrame(
                    data, index=[choice for choice in range(1, len(data['simple summary'])+1)]
                ) for dictionary in simple_summaries_master_list for data in dictionary.values()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 1.7
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [66]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, brief and isolated bouts of vigorous exercise performed multiple times throughout the day, are a promising strategy for improving cardiometabolic health. Research shows that exercise snacks involving cycling or stair climbing are effective in improving cardiorespiratory fitness ...   
2  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling and ...   
1  Hey! Have you heard of exercise snacks? It's a new strategy for improving cardiometabolic health by performing isolated bouts of brief vigorous exercise multiple times throughout the day. Research has shown that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling and...   
2  Hey, have you heard of exercise snacks? It's a new strategy to improve cardiometabolic health by performing i

In [67]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 1.7
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [72]:
qna_dict[iteration_id][0]

{0: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, brief and isolated bouts of vigorous exercise performed multiple times throughout the day, are a promising strategy for improving cardiometabolic health. Research shows that exercise snacks involving cycling or stair climbing are effective in improving cardiorespiratory fitness and exercise performance in inactive adults. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity and clinical populations, but more research is needed. The feasibility and efficacy of exercise snacks in a real-world setting and their potential to target musculoskeletal health remain to be determined.',
   'Exercise sna

In [71]:
pd.DataFrame(qna_dict[iteration_id][0]).transpose()

article_title  \
0  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

              summarization task  \
0  Summarize for a LinkedIn post   
1  Summarize for a LinkedIn post   

                                                                                                                                                                                                                                                                                                       summary  \
0  [Exercise snacks, brief and isolated bouts of vigorous exercise performed multiple times throughout the day, are a promising strategy for improving cardiometabolic health. Research shows that exercise snacks involving cycling or stair climbing are effective in improving cardiorespiratory fitness...   
1  [Exercise snacks, brief and isolated bouts of vigorous exercise performed multiple times throughout the day, are a promising strategy for improving cardiometabolic health. Research shows that exercise snacks involving cycling or stair climbing are effective in improving cardiorespiratory fitness...   

                          simplify task response_01  \
0  Make the language appropriate for a lay audience   
1  Make the language appropriate for a lay audience   

                          simplify task response_02  \
0  Make the language appropriate for a lay audience   
1  Make the language appropriate for a lay audience   

                                                                                                                                                                                                                                                                                                simple summary  \
0  [Exercise Snacks is a new approach to exercising that can improve our health. This approach involves doing short bursts of exercise throughout the day, instead of doing one long exercise session. In scientific studies, exercise snacks have been shown to improve our fitness and reduce the negativ...   
1  [Exercise Snacks is a new approach to exercising that can improve our health. This approach involves doing short bursts of exercise throughout the day, instead of doing one long exercise session. In scientific studies, exercise snacks have been shown to improve our fitness and reduce the negativ...   

                                                                                                                                                                                                                                                                                                          text  
0  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health\n\nTHE EFFICACY OF EXERCISE SNACKS FOR IMPROVING CRF IN INACTIVE ADULTS\n\nOur first exercise snacks study (15) was developed based on previous work showing a ~1 MET improvement in CRF after a 6-wk stair climbing protocol that in...  
1  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health\n\nTHE EFFICACY OF EXERCISE SNACKS FOR IMPROVING CRF IN INACTIVE ADULTS\n\nOur first exercise snacks study (15) was developed based on previous work showing a ~1 MET improvement in CRF after a 6-wk stair climbing protocol that in...

In [68]:
qna_dict[iteration_id]

[{0: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
   'system_role': 'You are an expert at science communication.',
   'model': 'gpt-3.5-turbo',
   'prep step': 'Take the key points and numerical descriptors to',
   'summarization task': 'Summarize for a LinkedIn post',
   'summary': ['Exercise snacks, brief and isolated bouts of vigorous exercise performed multiple times throughout the day, are a promising strategy for improving cardiometabolic health. Research shows that exercise snacks involving cycling or stair climbing are effective in improving cardiorespiratory fitness and exercise performance in inactive adults. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity and clinical populations, but more research is needed. The feasibility and efficacy of exercise snacks in a real-world setting and their potential to target musculoskeletal health remain to be determined.',
    'Exerc

## 1.8

In [73]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            # self.simplify_bot_dict[new_key] = Chaining(
            #     summary, system_role=system_role,
            #     model=model, temperature=temperature, max_tokens=max_tokens
            #     )
            simplify_prompt = self.create_prompt(simplify_task)
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)
            self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault(f'simple summary {new_key}', [])
        self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            qna_dict[iteration_id] = pd.concat([
                pd.DataFrame(
                    data, index=[choice for choice in range(1, len(data['simple summary'])+1)]
                ) for dictionary in simple_summaries_master_list for data in dictionary.values()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 1.8
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [74]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling and mo...   
2  Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, have emerged as a feasible and effective strategy for improving cardiometabolic health. Studies have shown that exercise snacks involving cycling and practical stair climbing are efficacious...   
1  Hey, have you heard about exercise snacks? They're isolated bouts of brief vigorous exercise that you can perform multiple times throughout the day. A study shows that three daily bouts of vigorous stair climbing performed 14 h apart on 3 d·wk?1 improved CRF and exercise performance in inactive...   
2  Hey, have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health by performin

In [75]:
qna_dict = prompt_chaining_dict(simplify_prompts[0], qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 1.8
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
An error occurred on line 331 in C:\Users\silvh\AppData\Local\Temp\ipykernel_26688\3984514522.py : 'simple summary'
Unable to create results DataFrame
**text1_prompt01
	...Prompt: Assume your audience has no science background., iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 cho

In [79]:
qna_dict[iteration_id][0]

{0: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~15\x9630 s of hard effort involving cycling and more practical stair climbing are efficacious for improving CRF and exercise performance in inactive adults. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity. However, their efficacy in clinical populations remains to be established as existing reports have studied a small number of participants in laboratory-based

In [78]:
pd.DataFrame(qna_dict[iteration_id][0])

0
article_title                                                                                                                                                                                                                                                                     Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health
model                                                                                                                                                                                                                                                                                                                                  gpt-3.5-turbo
prep step                                                                                                                                                                                                                                                                                           Take the key points and numerical descriptors to
simple summary simple_summary02_prompt1  [Exercise Snacks: A Quick and Easy Way to Boost Your Health\n\nAre you looking for a quick and easy way to improve your health? Exercise snacks might be the answer! Exercise snacks involve short bursts of vigorous exercise, performed multiple times throughout the day. This approach is based on r...
simplify task simple_summary01_prompt1                                                                                                                                                                                                                                                               Assume your audience has no science background.
simplify task simple_summary02_prompt1                                                                                                                                                                                                                                                               Assume your audience has no science background.
summarization task                                                                                                                                                                                                                                                                                                     Summarize for a LinkedIn post
summary                                  [Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling and m...
system_role                                                                                                                                                                                                                                                                                              You are an expert at science communication.
text                                     Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health\n\nTHE EFFICACY OF EXERCISE SNACKS FOR IMPROVING CRF IN INACTIVE ADULTS\n\nOur first exercise snacks study (15) was developed based on previous work showing a ~1 MET improvement in CRF after a 6-wk stair climbing protocol that in...

In [76]:
qna_dict[iteration_id]

[{0: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
   'system_role': 'You are an expert at science communication.',
   'model': 'gpt-3.5-turbo',
   'prep step': 'Take the key points and numerical descriptors to',
   'summarization task': 'Summarize for a LinkedIn post',
   'summary': ['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~15\x9630 s of hard effort involving cycling and more practical stair climbing are efficacious for improving CRF and exercise performance in inactive adults. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity. However, their efficacy in clinical populations remains to be established as existing reports have studied a small number of participants in laboratory

## 1.9

In [8]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([{key, value} for key, value in self.summaries_dict.items()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            # self.simplify_bot_dict[new_key] = Chaining(
            #     summary, system_role=system_role,
            #     model=model, temperature=temperature, max_tokens=max_tokens
            #     )
            simplify_prompt = self.create_prompt(simplify_task)
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault(f'simple summary {new_key}', [])
        self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data #, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            qna_dict[iteration_id] = pd.concat([
                pd.DataFrame(
                    data, index=[choice for choice in range(1, len(data['simple summary'])+1)]
                ) for dictionary in simple_summaries_master_list for data in dictionary.values()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 1.9
n_choices = 2
qna_dict = dict()
chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [10]:
qna_dict[iteration_id]

article_title  \
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

                                                     summarization task  \
0                                         Summarize for a LinkedIn post   
1                                         Summarize for a LinkedIn post   
0  Describe the interesting points to your coworker at the water cooler   
1  Describe the interesting points to your coworker at the water cooler   
0                                         Summarize for a LinkedIn post   
1                                         Summarize for a LinkedIn post   
0  Describe the interesting points to your coworker at the water cooler   
1  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
0  {Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling and more practica...   
1  {Exercise Snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, can be a feasible and effective strategy to improve cardio-metabolic health. A study by the American College of Sports Medicine showed that exercise snacks consisting of three daily bouts o...   
0  {Hey there! Have you heard about exercise snacks? It's a new strategy to improve our cardiometabolic health. Studies have shown that brief bursts of vigorous exercise, lasting around 15-30 seconds, performed multiple times throughout the day can improve our cardiorespiratory fitness (CRF) and re...   
1  {Hey! Have you heard about exercise snacks? It's a new strategy that involves isolated bouts of brief vigorou

In [12]:
chatbot_dict[iteration_id]['text1_prompt00'].qna

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': [{'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks involving thrice daily ~15\x9630 s of hard effort involving cycling and more practical stair climbing are efficacious for improving cardiorespiratory fitness and exercise performance in inactive adults. They also have the potential to improve aspects of cardiometabolic health in individuals with obesity. The applicability of exercise snacks in a real-world setting and their potential to target musculoskeletal health are yet to be determined.',
   'response_01'},
  {'E

In [13]:
chatbot_dict[iteration_id]['text1_prompt00'].qna['summary']

[{'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks involving thrice daily ~15\x9630 s of hard effort involving cycling and more practical stair climbing are efficacious for improving cardiorespiratory fitness and exercise performance in inactive adults. They also have the potential to improve aspects of cardiometabolic health in individuals with obesity. The applicability of exercise snacks in a real-world setting and their potential to target musculoskeletal health are yet to be determined.',
  'response_01'},
 {'Exercise Snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, can be a feasible and effective strategy to improve cardio-metabolic health. A study by the American College of Sports Medicine showed that exercise snacks consisting of three daily bouts of vigorous stair cli

# Iteration 2

In [14]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([{key: value} for key, value in self.summaries_dict.items()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            # self.simplify_bot_dict[new_key] = Chaining(
            #     summary, system_role=system_role,
            #     model=model, temperature=temperature, max_tokens=max_tokens
            #     )
            simplify_prompt = self.create_prompt(simplify_task)
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        # self.qna.setdefault(f'simple summary {new_key}', [])
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        self.qna['simple summary'] = dict()
        self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data #, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            qna_dict[iteration_id] = pd.concat([
                pd.DataFrame(
                    data, index=[choice for choice in range(1, len(data['simple summary'])+1)]
                ) for dictionary in simple_summaries_master_list for data in dictionary.values()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 2
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [15]:
qna_dict[iteration_id]

article_title  \
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

                                                     summarization task  \
0                                         Summarize for a LinkedIn post   
1                                         Summarize for a LinkedIn post   
0  Describe the interesting points to your coworker at the water cooler   
1  Describe the interesting points to your coworker at the water cooler   
0                                         Summarize for a LinkedIn post   
1                                         Summarize for a LinkedIn post   
0  Describe the interesting points to your coworker at the water cooler   
1  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
0  {'response_01': 'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in previously inactive adults. Studies have shown that thrice-daily 15-30 seconds of hard effort involv...   
1  {'response_02': 'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving thrice daily ~1530 s of hard effort involving cycli...   
0  {'response_01': 'Hey! Have you heard of exercise snacks? It's a new strategy to improve cardiometabolic health. The idea is to have isolated bouts of brief, vigorous exercise multiple times throughout the day. Studies have shown that even just a few minutes of intense stair climbing or cycling c...   
1  {'response_02': 'Hey there! Have you heard of exercise snacks? They're defined as isolated bouts of brief vig

In [16]:
chatbot_dict[iteration_id]['text1_prompt00'].qna

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': [{'response_01': 'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in previously inactive adults. Studies have shown that thrice-daily 15-30 seconds of hard effort involving cycling and stair climbing can improve cardiorespiratory fitness and exercise performance. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity and are aligned with the revised Physical Activity Guidelines for Americans and the WHO Guidelines on Physical Activity and Sedentary Behavior. Further research is needed to determine

In [30]:
simplify_prompts

['Assume your audience has no science background.',
 'Make the language appropriate for a lay audience']

In [17]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 2
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparin

In [20]:
chatbot_dict[iteration_id]['text1_prompt00'].qna

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': [{'response_01': 'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in previously inactive adults. Studies have shown that thrice-daily 15-30 seconds of hard effort involving cycling and stair climbing can improve cardiorespiratory fitness and exercise performance. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity and are aligned with the revised Physical Activity Guidelines for Americans and the WHO Guidelines on Physical Activity and Sedentary Behavior. Further research is needed to determine

In [29]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict

{'simple_summary01_prompt1_option01': "Exercise Snacks are a new way to improve your health through short bursts of exercise throughout the day. Studies have shown that even just a few minutes of vigorous stair climbing or cycling can improve your cardiovascular fitness and performance. These exercise snacks can be done at home, at work, or even during a break between virtual meetings. They don't require specialized equipment or all-out efforts, and the health benefits can still be achieved. Exercise snacks are also a great way to combat sedentary behavior and improve metabolic health in individuals with obesity or other health conditions. While more research is needed to fully understand their potential, exercise snacks show promise as a simple and effective way to improve your overall health.",
 'simple_summary01_prompt1_option02': "Have you heard of exercise snacks? It's a new way to improve your heart and metabolic health by doing brief bouts of vigorous exercise throughout the day

In [24]:
print(len(qna_dict[iteration_id][0][0]['simple summary']))
qna_dict[iteration_id][0][0]['simple summary']

1


{1: ["Exercise Snacks are a new way to improve your health through short bursts of exercise throughout the day. Studies have shown that even just a few minutes of vigorous stair climbing or cycling can improve your cardiovascular fitness and performance. These exercise snacks can be done at home, at work, or even during a break between virtual meetings. They don't require specialized equipment or all-out efforts, and the health benefits can still be achieved. Exercise snacks are also a great way to combat sedentary behavior and improve metabolic health in individuals with obesity or other health conditions. While more research is needed to fully understand their potential, exercise snacks show promise as a simple and effective way to improve your overall health.",
  "Have you heard of exercise snacks? It's a new way to improve your heart and metabolic health by doing brief bouts of vigorous exercise throughout the day. In a recent study, researchers found that just three daily bouts of

In [27]:
qna_dict[iteration_id][0]

{0: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': [{'response_01': 'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in previously inactive adults. Studies have shown that thrice-daily 15-30 seconds of hard effort involving cycling and stair climbing can improve cardiorespiratory fitness and exercise performance. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity and are aligned with the revised Physical Activity Guidelines for Americans and the WHO Guidelines on Physical Activity and Sedentary Behavior. Further research is needed to 

In [26]:
pd.DataFrame(qna_dict[iteration_id][0])

0  \
article_title                                                                                                                                                                                                                                                Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
system_role                                                                                                                                                                                                                                                                         You are an expert at science communication.   
model                                                                                                                                                                                                                                                                                                             gpt-3.5-turbo   
prep step                                                                                                                                                                                                                                                                      Take the key points and numerical descriptors to   
summarization task                                                                                                                                                                                                                                                                                Summarize for a LinkedIn post   
summary             [{'response_01': 'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in previously inactive adults. Studies have shown that thrice-daily 15-30 seconds of hard effort invol...   
simple summary      {1: ['Exercise Snacks are a new way to improve your health through short bursts of exercise throughout the day. Studies have shown that even just a few minutes of vigorous stair climbing or cycling can improve your cardiovascular fitness and performance. These exercise snacks can be done at home...   
text                Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health\n\nTHE EFFICACY OF EXERCISE SNACKS FOR IMPROVING CRF IN INACTIVE ADULTS\n\nOur first exercise snacks study (15) was developed based on previous work showing a ~1 MET improvement in CRF after a 6-wk stair climbing protocol that in...   

                                                                                                                                                                                                                                                                                                                              1  
article_title                                                                                                                                                                                                                                                Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health  
system_role                                                                                                                                                                                                                                                                         You are an expert at science communication.  
model                                                                                                                                                                                                                                                                                                             gpt-3.5-turbo  
prep step                                                                                                                 

In [19]:
qna_dict[iteration_id]

[{0: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
   'system_role': 'You are an expert at science communication.',
   'model': 'gpt-3.5-turbo',
   'prep step': 'Take the key points and numerical descriptors to',
   'summarization task': 'Summarize for a LinkedIn post',
   'summary': [{'response_01': 'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in previously inactive adults. Studies have shown that thrice-daily 15-30 seconds of hard effort involving cycling and stair climbing can improve cardiorespiratory fitness and exercise performance. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity and are aligned with the revised Physical Activity Guidelines for Americans and the WHO Guidelines on Physical Activity and Sedentary Behavior. Further research is need

## 2.1

In [33]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simplify_bot_dict = dict()
        self.simple_summary_dict = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            # self.simplify_bot_dict[new_key] = Chaining(
            #     summary, system_role=system_role,
            #     model=model, temperature=temperature, max_tokens=max_tokens
            #     )
            simplify_prompt = self.create_prompt(simplify_task)
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault('simple summary', {})
        self.qna['simple summary'].setdefault(simplify_iteration, [])
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            qna_dict[iteration_id] = pd.concat([
                pd.DataFrame(
                    data, index=[choice for choice in range(1, len(data['simple summary'])+1)]
                ) for dictionary in simple_summaries_master_list for data in dictionary.values()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 2.1
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [34]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy for improving cardiometabolic health. Studies have shown that exercise snacks can improve cardiorespiratory fitness and exercise performance in inactive adults, ...   
2  Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, have been shown to improve cardiometabolic health in previously inactive adults. These isolated bouts of exercise involve cycling or stair climbing and can be easily implemented in a home, s...   
1  Hey! Have you heard of exercise snacks? They're brief, vigorous bouts of exercise that you can perform multiple times throughout the day. Studies have shown that exercise snacks are an effective strategy for improving cardiorespiratory fitness and exercise performance in inactive adults. They're...   
2  Hey, have you heard of exercise snacks? It's a new strategy to improve cardiometabolic health by performing i

In [35]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 2.1
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [39]:
print(len(qna_dict[iteration_id][0]))
qna_dict[iteration_id][0][0]

2


{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy for improving cardiometabolic health. Studies have shown that exercise snacks can improve cardiorespiratory fitness and exercise performance in inactive adults, as well as mitigate the negative effects of prolonged sitting on metabolic markers. Exercise snacks also align with the revised Physical Activity Guidelines for Americans and the World Health Organization Guidelines on Physical Activity and Sedentary Behavior. Further research is needed to establish the efficacy of exercise snacks in clinical populations and their potential to improve mu

In [41]:
qna_dict[iteration_id][0][0].keys()

dict_keys(['article_title', 'system_role', 'model', 'prep step', 'summarization task', 'summary', 'simple summary', 'text'])

In [40]:
pd.DataFrame(qna_dict[iteration_id][0][0])

ValueError: Mixing dicts with non-Series may lead to ambiguous ordering.

In [36]:
qna_dict[iteration_id]

[{0: {'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
   'system_role': 'You are an expert at science communication.',
   'model': 'gpt-3.5-turbo',
   'prep step': 'Take the key points and numerical descriptors to',
   'summarization task': 'Summarize for a LinkedIn post',
   'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy for improving cardiometabolic health. Studies have shown that exercise snacks can improve cardiorespiratory fitness and exercise performance in inactive adults, as well as mitigate the negative effects of prolonged sitting on metabolic markers. Exercise snacks also align with the revised Physical Activity Guidelines for Americans and the World Health Organization Guidelines on Physical Activity and Sedentary Behavior. Further research is needed to establish the efficacy of exercise snacks in clinical populations and their potentia

# Iteration 3 Change how batch_summary_dict works for multiple summary prompts

In [44]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simple_summary_dict.setdefault(f'{simplify_iteration}', {})
        self.simple_summary_dict[f'{simplify_iteration}'] = self.qna
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{simplify_iteration}'][f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[f'{simplify_iteration}'][new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault(f'simple summary', [])
        self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[f'{simplify_iteration}'].values()])
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            qna_dict[iteration_id] = pd.concat([
                pd.DataFrame(
                    data#, index=[choice for choice in range(1, len(data['simple summary'])+1)]
                ) for dictionary in simple_summaries_master_list for data in dictionary.values()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 3
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [45]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks are a novel approach to improving cardiometabolic health through brief bouts of vigorous exercise performed multiple times throughout the day. Studies have shown that short sessions of stair climbing or cycling can improve cardiorespiratory fitness and metabolic markers in previo...   
2  Exercise snacks, defined as short bouts of vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving cycling or stair climbing can improve cardiorespiratory fitness and exercise p...   
1  Hey! Have you heard about the concept of "exercise snacks"? It's a new strategy to improve cardiometabolic health. Basically, it involves performing isolated bouts of brief vigorous exercise multiple times throughout the day. There have been studies that show exercise snacks, involving either cy...   
2  Hey! Have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health. The idea is

In [ ]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

In [ ]:
qna_dict[iteration_id]

## 3.1

In [ ]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for key, value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simple_summary_dict.setdefault(f'{simplify_iteration}', {})
        self.simple_summary_dict[f'{simplify_iteration}'] = self.qna
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.simple_summary_dict[f'{simplify_iteration}'][f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[f'{simplify_iteration}'][new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault(f'simple summary', [])
        self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[f'{simplify_iteration}'].values()])
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            # updated_qna_dict = pd.Series(temp_qna_dict[key])
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            qna_dict[iteration_id] = pd.concat([
                pd.DataFrame(
                    data#, index=[choice for choice in range(1, len(data['simple summary'])+1)]
                ) for dictionary in simple_summaries_master_list for data in dictionary.values()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 3
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
An error occurred on line 94 in C:\Users\silvh\AppData\Local\Temp\ipykernel_13880\1467514554.py : too many values to unpack (expected 2)
	**Error with response parsing**
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
An error occurred on line 94 in C:\Users\silvh\AppData\Local\Temp\ipykernel_13880\1467514554.py : too many values to unpack (expected 2)
	**Error with response parsing**
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaini

In [46]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks are a novel approach to improving cardiometabolic health through brief bouts of vigorous exercise performed multiple times throughout the day. Studies have shown that short sessions of stair climbing or cycling can improve cardiorespiratory fitness and metabolic markers in previo...   
2  Exercise snacks, defined as short bouts of vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving cycling or stair climbing can improve cardiorespiratory fitness and exercise p...   
1  Hey! Have you heard about the concept of "exercise snacks"? It's a new strategy to improve cardiometabolic health. Basically, it involves performing isolated bouts of brief vigorous exercise multiple times throughout the day. There have been studies that show exercise snacks, involving either cy...   
2  Hey! Have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health. The idea is

In [47]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3


AttributeError: 'Chaining' object has no attribute 'simplify_bot_dict'

## 3.2

In [50]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simple_summary_dict.setdefault(f'{simplify_iteration}', {})
        self.simple_summary_dict[f'{simplify_iteration}'] = self.qna
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    response_dict = dict()
                    response_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    self.simple_summary_dict[f'{simplify_iteration}'] = response_dict
                    print(f'\t...Summary given')
            except:
                self.simple_summary_dict[f'{simplify_iteration}'][new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault(f'simple summary', [])
        self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[f'{simplify_iteration}'].values()])
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            qna_dict[iteration_id] = pd.concat([
                pd.DataFrame(
                    data#, index=[choice for choice in range(1, len(data['simple summary'])+1)]
                ) for dictionary in simple_summaries_master_list for data in dictionary.values()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    # try:
        # qna_chain_dict[summary_iteration_id].columns = [i for i in range(len(qna_chain_dict[summary_iteration_id].columns))]
        # temp_qna_chain_dict = pd.concat([
        #     qna_chain_dict[summary_iteration_id], 
        #     simple_summaries_df
        #     ])
    #     temp_qna_chain_dict = pd.concat([
    #         pd.DataFrame(
    #             data, index=
    #         )
    #     ])
    #     qna_chain_dict[iteration_id] = temp_qna_chain_dict
    #     print(f"{'Simple summaries' if prompt_column=='simplify' else 'Article relevance for user'} added to original DataFrame")
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 3.2
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [51]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in the general population. Emerging evidence shows that exercise snacks involving thrice-daily ~15-30 seconds of hard ef...   
2  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy for improving cardiometabolic health. Studies have shown that exercise snacks can improve cardiorespiratory fitness and exercise performance in inactive...   
1  Hey, have you heard of exercise snacks? It's a new strategy to improve cardiometabolic health that involves isolated bouts of brief vigorous exercise performed multiple times throughout the day. According to recent studies, exercise snacks involving thrice daily ~1530 s of hard effort involving...   
2  Hey, have you heard of exercise snacks? It's a new strategy to improve cardiometabolic health! Basically, it 

In [52]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3.2
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [61]:
chatbot_dict[iteration_id]['text1_prompt00'].qna

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': ['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in the general population. Emerging evidence shows that exercise snacks involving thrice-daily ~15-30 seconds of hard effort involving cycling or stair climbing are efficacious for improving cardiorespiratory fitness and exercise performance in inactive adults. These findings suggest that exercise snacks could be a promising avenue for future research into improving metabolic outcomes in clinical populations.',
  'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple tim

In [66]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict

{'0': {'simple_summary02_prompt0_option02': "Exercise snacks are a new way to improve your health by doing short bursts of exercise throughout the day. This article talks about studies that show how doing just a few minutes of vigorous exercise, like climbing stairs or cycling, can improve your fitness and reduce the negative effects of sitting for long periods. These exercise snacks can be done at home, work, or school and don't require any special equipment. They can be a great way to add more physical activity into your day and improve your overall health."},
 '1': {'simple_summary02_prompt1_option02': "Exercise snacks are a new way to improve your heart and metabolic health. Basically, they are short bursts of exercise that you can do throughout the day. Studies have shown that even just a few minutes of vigorous exercise, like climbing stairs or cycling, can improve your cardiorespiratory fitness (CRF) and exercise performance. This is especially important for people who are inact

### reference: df with simple summary 

In [57]:
print(pd.concat([pd.DataFrame(value) for value in qna_dict[iteration_id]]).shape)
pd.concat([pd.DataFrame(value) for value in qna_dict[iteration_id]])

(16, 8)


article_title  \
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

                                                     summarization task  \
0                                         Summarize for a LinkedIn post   
1             

In [53]:
qna_dict[iteration_id]

[{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in the general population. Emerging evidence shows that exercise snacks involving thrice-daily ~15-30 seconds of hard effort involving cycling or stair climbing are efficacious for improving cardiorespiratory fitness and exercise performance in inactive adults. These findings suggest that exercise snacks could be a promising avenue for future research into improving metabolic outcomes in clinical populations.',
   'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multi

In [58]:
qna_dict[iteration_id+0.001]

[{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in the general population. Emerging evidence shows that exercise snacks involving thrice-daily ~15-30 seconds of hard effort involving cycling or stair climbing are efficacious for improving cardiorespiratory fitness and exercise performance in inactive adults. These findings suggest that exercise snacks could be a promising avenue for future research into improving metabolic outcomes in clinical populations.',
   'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multi

## 3.3

In [67]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simple_summary_dict[simplify_iteration] = self.qna
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                response_dict = dict()
                for index, choice in enumerate(response.choices):
                    response_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
                response_dict['simplify task'] = simplify_task
                self.simple_summary_dict[simplify_iteration] = response_dict
            except:
                self.simple_summary_dict[simplify_iteration][new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault(f'simple summary', [])
        self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[simplify_iteration].values()])
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_df = pd.DataFrame()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])


            # simple_summaries_master_dict[text_prompt_key] = {**simple_summaries_master_dict[text_prompt_key], **summary_dict}
        try:
            qna_dict[iteration_id] = pd.concat([
                pd.DataFrame(data) for dictionary in simple_summaries_master_list for data in dictionary.values()
            ])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Unable to create results DataFrame')
            
            qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    #     if save_outputs:
    #         try:
    #             save_output(
    #                 qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #                 csv_path=csv_path, pickle_path=pickle_path)
    #             save_output(
    #                 chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #                 csv_path=None, pickle_path=pickle_path)
    #         except:
    #             print('[prompt_chaining_dict()] Unable to save outputs')
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to concatenate simple summary DataFrame to original DataFrame')
    #     qna_chain_dict[iteration_id+0.001] = simple_summaries_master_dict
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 3.3
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [68]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, can be a feasible and effective strategy to improve cardiometabolic health in previously inactive adults. Studies have shown that exercise snacks involving cycling or stair climbing can impr...   
2  Exercise snacks, defined as short bouts of vigorous exercise performed multiple times throughout the day, may be a feasible strategy to simultaneously improve cardiometabolic health and physical fitness. Emerging evidence suggests that exercise snacks involving cycling or practical stair climbin...   
1  Hey! Have you heard of exercise snacks? They're isolated bouts of brief, vigorous exercise performed multiple times throughout the day. It turns out that exercise snacks involving thrice daily 15-30 seconds of hard effort involving cycling and more practical stair climbing are efficacious for im...   
2  Hey, have you heard of "exercise snacks"? It's a new concept where people perform short, intense bouts of exe

In [69]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3.3
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [72]:
print(len(chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict))
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict

4


{0: {'simple_summary02_prompt0_option01': "Exercise snacks are a new way of getting exercise that can help improve your heart and metabolic health. These snacks involve short bursts of intense exercise that you can do throughout the day, such as climbing stairs quickly or doing jumping jacks. Studies have shown that exercise snacks can improve your fitness and performance, as well as reduce the negative effects of sitting for long periods of time. They can also be a good option for people who don't have a lot of time for exercise or who may have health issues that make traditional exercise difficult.",
  'simple_summary02_prompt0_option02': 'Exercise snacks are short bursts of vigorous exercise that can be performed multiple times throughout the day. Recent studies have shown that exercise snacks can improve cardiometabolic health and increase exercise performance in previously inactive adults. These exercise snacks involve either cycling or stair climbing for a short period of time, w

In [73]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict[0]

{'simple_summary02_prompt0_option01': "Exercise snacks are a new way of getting exercise that can help improve your heart and metabolic health. These snacks involve short bursts of intense exercise that you can do throughout the day, such as climbing stairs quickly or doing jumping jacks. Studies have shown that exercise snacks can improve your fitness and performance, as well as reduce the negative effects of sitting for long periods of time. They can also be a good option for people who don't have a lot of time for exercise or who may have health issues that make traditional exercise difficult.",
 'simple_summary02_prompt0_option02': 'Exercise snacks are short bursts of vigorous exercise that can be performed multiple times throughout the day. Recent studies have shown that exercise snacks can improve cardiometabolic health and increase exercise performance in previously inactive adults. These exercise snacks involve either cycling or stair climbing for a short period of time, with a

In [74]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict[1]

{'simple_summary02_prompt1_option01': "Exercise snacks are a new and exciting way to improve our health. They involve doing short bursts of vigorous exercise throughout the day, which can help us become healthier even if we're not able to do a lot of exercise at once. Studies have shown that exercise snacks can improve our cardiovascular fitness and help us perform better during exercise. They can also help us break up long periods of sitting, which has been linked to health problems like type 2 diabetes and heart disease. Exercise snacks involve activities like climbing stairs quickly or doing short bursts of cycling. They don't require any special equipment and can be done at home, work, or school. Although more research is needed, exercise snacks could be a great way to improve our health and fitness in a fun and easy way.",
 'simple_summary02_prompt1_option02': 'Exercise snacks are short bursts of vigorous exercise that can be performed throughout the day. Recent studies have shown

In [77]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict['1']

'Make the language appropriate for a lay audience'

In [76]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict.keys()

dict_keys([0, '0', 1, '1'])

In [71]:
qna_dict[iteration_id]

[{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, can be a feasible and effective strategy to improve cardiometabolic health in previously inactive adults. Studies have shown that exercise snacks involving cycling or stair climbing can improve cardiorespiratory fitness, metabolic control, and vascular function. The approach aligns with the updated Physical Activity Guidelines for Americans and the World Health Organization Guidelines on Physical Activity and Sedentary Behavior. While the efficacy of exercise snacks in clinical populations needs further examination, they offer a practical and accessible option for imp

## 3.4

In [78]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simple_summary_dict[simplify_iteration] = self.qna
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                response_dict = dict()
                for index, choice in enumerate(response.choices):
                    response_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
                response_dict['simplify task'] = simplify_task
                self.simple_summary_dict[simplify_iteration] = response_dict
            except:
                self.simple_summary_dict[simplify_iteration][new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault(f'simple summary', [])
        self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[simplify_iteration].values()])
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(data) for data in simple_summaries_master_list
        ])
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to create results DataFrame')
        
        qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    if save_outputs:
        try:
            save_output(
                qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                csv_path=csv_path, pickle_path=pickle_path)
            save_output(
                chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                csv_path=None, pickle_path=pickle_path)
        except:
            print('[prompt_chaining_dict()] Unable to save outputs')
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 3.4
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [79]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as brief, isolated bouts of vigorous exercise performed multiple times throughout the day, have shown promise in improving cardiorespiratory fitness and reducing the impact of sedentariness on cardiometabolic health. Studies have demonstrated the efficacy of exercise sna...   
2  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling and st...   
1  Hey, have you heard of exercise snacks? It's a new strategy for improving cardiometabolic health! Basically, it involves doing short bursts of hard exercise multiple times throughout the day. Studies have shown that even just three bouts of vigorous stair climbing performed 1-4 hours apart on 3 ...   
2  Hey there! Have you heard of exercise snacks? It's a new strategy for improving cardiovascular and metabolic 

In [80]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3.4
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [81]:
print(len(chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict))
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict

2


{0: {'simple_summary02_prompt0_option01': 'Exercise snacks are short bursts of intense physical activity that can be performed multiple times throughout the day. They are a new strategy to improve cardiometabolic health in previously inactive adults. Studies show that even a few minutes of vigorous stair climbing or cycling can improve cardiorespiratory fitness (CRF) and exercise performance. Exercise snacks can also disrupt prolonged periods of inactivity and improve markers of metabolic control in individuals with obesity or type 2 diabetes. They may also have potential to improve vascular health by increasing blood flow and shear stress. Exercise snacks can be easily incorporated into daily routines and are aligned with the latest physical activity guidelines. However, further research is needed to determine their efficacy in clinical populations and their potential to target musculoskeletal health.',
  'simple_summary02_prompt0_option02': "Exercise snacks are a new way to improve o

In [84]:
# print(pd.concat([pd.DataFrame(value) for value in qna_dict[iteration_id]]).shape)
pd.concat([pd.DataFrame(value) for value in qna_dict[iteration_id]])

ValueError: All arrays must be of the same length

In [86]:
pd.DataFrame(qna_dict[iteration_id][0])

ValueError: All arrays must be of the same length

In [91]:
print(len(qna_dict[iteration_id][0]['simple summary']))
qna_dict[iteration_id][0]['simple summary']

6


['Exercise snacks are short bursts of intense physical activity that can be performed multiple times throughout the day. They are a new strategy to improve cardiometabolic health in previously inactive adults. Studies show that even a few minutes of vigorous stair climbing or cycling can improve cardiorespiratory fitness (CRF) and exercise performance. Exercise snacks can also disrupt prolonged periods of inactivity and improve markers of metabolic control in individuals with obesity or type 2 diabetes. They may also have potential to improve vascular health by increasing blood flow and shear stress. Exercise snacks can be easily incorporated into daily routines and are aligned with the latest physical activity guidelines. However, further research is needed to determine their efficacy in clinical populations and their potential to target musculoskeletal health.',
 "Exercise snacks are a new way to improve our health through short bursts of vigorous exercise throughout the day. These e

In [82]:
qna_dict[iteration_id]

[{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as brief, isolated bouts of vigorous exercise performed multiple times throughout the day, have shown promise in improving cardiorespiratory fitness and reducing the impact of sedentariness on cardiometabolic health. Studies have demonstrated the efficacy of exercise snacks in improving CRF and exercise performance in inactive adults, as well as reducing insulin and nonesterified fatty acids in individuals with obesity. The potential for exercise snacks to improve vascular health has also been explored. While exercise snacks align with revised physical activity guidelines, their applicability in a real-world setting and efficacy in clinical popula

## 3.5

In [92]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simple_summary_dict[simplify_iteration] = self.qna
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                response_dict = dict()
                for index, choice in enumerate(response.choices):
                    response_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
                # response_dict['simplify task'] = simplify_task
                self.simple_summary_dict[simplify_iteration] = response_dict

            except:
                self.simple_summary_dict[simplify_iteration][new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        self.qna.setdefault(f'simple summary', [])
        self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[simplify_iteration].values()])
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(data) for data in simple_summaries_master_list
        ])
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to create results DataFrame')
        
        qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    if save_outputs:
        try:
            save_output(
                qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                csv_path=csv_path, pickle_path=pickle_path)
            save_output(
                chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                csv_path=None, pickle_path=pickle_path)
        except:
            print('[prompt_chaining_dict()] Unable to save outputs')
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 3.5
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [93]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving thrice daily ~15-30 seconds of hard effort involving cycling and pr...   
2  Exercise snacks, defined as brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health, according to a recent article published in the journal Medicine & Science in Sports & Exercise. Studies have shown that exercise snacks i...   
1  Hey, have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health that involves isolated bouts of brief, vigorous exercise performed multiple times throughout the day. Studies have shown that exercise snacks can improve cardiorespiratory fitness and exercise perfor...   
2  Hey, have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health by performin

In [94]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3.5
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [101]:
chatbot_dict[iteration_id]['text1_prompt00'].qna

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': ['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving thrice daily ~15-30 seconds of hard effort involving cycling and practical stair climbing are efficacious for improving cardiorespiratory fitness and exercise performance in inactive adults. They may also have potential to improve aspects of cardiometabolic health in individuals with obesity. The applicability of exercise snacks in a real-world setting and their potential to target musculoskeletal health remain to be determined.',
  'Exercise snacks, de

In [100]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict

{0: {'simple_summary02_prompt0_option01': 'Exercise snacks are a new and innovative way to improve our health. They involve short bursts of vigorous exercise, such as climbing stairs or cycling, performed several times throughout the day. Studies have shown that exercise snacks can improve our cardiorespiratory fitness (CRF) and exercise performance, even in inactive adults. They are also a feasible strategy for breaking up prolonged periods of sitting and improving metabolic markers in preclinical and clinical populations. In addition, exercise snacks may have potential to improve our vascular health. The concept of exercise snacks aligns with the latest physical activity guidelines that emphasize the importance of short bouts of physical activity. While exercise snacks require some planning and structure, they are a practical and accessible way to improve our health.',
  'simple_summary02_prompt0_option02': 'Exercise Snacks are short bouts of physical activity that can be done multip

In [104]:
pd.DataFrame(chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict[0], index=[0])

simple_summary02_prompt0_option01  \
0  Exercise snacks are a new and innovative way to improve our health. They involve short bursts of vigorous exercise, such as climbing stairs or cycling, performed several times throughout the day. Studies have shown that exercise snacks can improve our cardiorespiratory fitness (CRF) and exercise...   

                                                                                                                                                                                                                                                                             simple_summary02_prompt0_option02  \
0  Exercise Snacks are short bouts of physical activity that can be done multiple times throughout the day to improve our health. These exercise snacks are brief, isolated and vigorous exercises that can be done anywhere, including home, school or office. They are designed to break up prolonged per...   

                                     simplify task  
0  Assume your audience has no science background.

In [98]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict[0]

{'simple_summary02_prompt0_option01': 'Exercise snacks are a new and innovative way to improve our health. They involve short bursts of vigorous exercise, such as climbing stairs or cycling, performed several times throughout the day. Studies have shown that exercise snacks can improve our cardiorespiratory fitness (CRF) and exercise performance, even in inactive adults. They are also a feasible strategy for breaking up prolonged periods of sitting and improving metabolic markers in preclinical and clinical populations. In addition, exercise snacks may have potential to improve our vascular health. The concept of exercise snacks aligns with the latest physical activity guidelines that emphasize the importance of short bouts of physical activity. While exercise snacks require some planning and structure, they are a practical and accessible way to improve our health.',
 'simple_summary02_prompt0_option02': 'Exercise Snacks are short bouts of physical activity that can be done multiple ti

In [96]:
qna_dict[iteration_id][0]

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': ['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving thrice daily ~15-30 seconds of hard effort involving cycling and practical stair climbing are efficacious for improving cardiorespiratory fitness and exercise performance in inactive adults. They may also have potential to improve aspects of cardiometabolic health in individuals with obesity. The applicability of exercise snacks in a real-world setting and their potential to target musculoskeletal health remain to be determined.',
  'Exercise snacks, de

In [ ]:
qna_dict[iteration_id]

[{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving thrice daily ~15-30 seconds of hard effort involving cycling and practical stair climbing are efficacious for improving cardiorespiratory fitness and exercise performance in inactive adults. They may also have potential to improve aspects of cardiometabolic health in individuals with obesity. The applicability of exercise snacks in a real-world setting and their potential to target musculoskeletal health remain to be determined.',
   'Exercise sna

## 3.6

In [105]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simple_summary_dict[simplify_iteration] = self.qna
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                response_dict = dict()
                for index, choice in enumerate(response.choices):
                    response_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
                # response_dict['simplify task'] = simplify_task
                self.simple_summary_dict[simplify_iteration] = response_dict

            except:
                self.simple_summary_dict[simplify_iteration][new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        # self.qna.setdefault(f'simple summary', [])
        # self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[simplify_iteration].values()])
        self.qna[f'simple summary'] = self.simple_summary_dict[simplify_iteration]
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(data) for data in simple_summaries_master_list
        ])
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to create results DataFrame')
        
        qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    if save_outputs:
        try:
            save_output(
                qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                csv_path=csv_path, pickle_path=pickle_path)
            save_output(
                chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                csv_path=None, pickle_path=pickle_path)
        except:
            print('[prompt_chaining_dict()] Unable to save outputs')
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 3.6
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [106]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3.6
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [111]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict

{0: {'simple_summary02_prompt0_option01': "Exercise Snacks are a type of exercise that involves doing short and intense bursts of physical activity multiple times throughout the day. This is a new and innovative way to improve our health and fitness. The research shows that even small amounts of exercise, like climbing stairs or doing jumping jacks, can make a big difference in our overall health. Exercise Snacks can improve our heart and lung fitness, lower our risk of developing diseases like diabetes, and even improve our blood flow. These exercises are easy to do at home or work, and they don't take much time or effort. By incorporating Exercise Snacks into our daily routine, we can improve our health and well-being.",
  'simple_summary02_prompt0_option02': 'Exercise Snacks are a new and innovative strategy that can help improve our heart health and metabolism. The idea behind it is to perform short bouts of vigorous exercise throughout the day instead of long periods, making it ea

In [113]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict[0]

{'simple_summary02_prompt0_option01': "Exercise Snacks are a type of exercise that involves doing short and intense bursts of physical activity multiple times throughout the day. This is a new and innovative way to improve our health and fitness. The research shows that even small amounts of exercise, like climbing stairs or doing jumping jacks, can make a big difference in our overall health. Exercise Snacks can improve our heart and lung fitness, lower our risk of developing diseases like diabetes, and even improve our blood flow. These exercises are easy to do at home or work, and they don't take much time or effort. By incorporating Exercise Snacks into our daily routine, we can improve our health and well-being.",
 'simple_summary02_prompt0_option02': 'Exercise Snacks are a new and innovative strategy that can help improve our heart health and metabolism. The idea behind it is to perform short bouts of vigorous exercise throughout the day instead of long periods, making it easier 

In [112]:
pd.DataFrame(chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict)

0  \
simple_summary02_prompt0_option01  Exercise Snacks are a type of exercise that involves doing short and intense bursts of physical activity multiple times throughout the day. This is a new and innovative way to improve our health and fitness. The research shows that even small amounts of exercise, like climbing stairs or doing ju...   
simple_summary02_prompt0_option02  Exercise Snacks are a new and innovative strategy that can help improve our heart health and metabolism. The idea behind it is to perform short bouts of vigorous exercise throughout the day instead of long periods, making it easier to incorporate into our daily routine. The exercises can be as s...   
simplify task                                                                                                                                                                                                                                                                                  Assume your audience has no science background.   
simple_summary02_prompt1_option01                                                                                                                                                                                                                                                                                                          NaN   
simple_summary02_prompt1_option02                                                                                                                                                                                                                                                                                                          NaN   

                                                                                                                                                                                                                                                                                                                                             1  
simple_summary02_prompt0_option01                                                                                                                                                                                                                                                                                                          NaN  
simple_summary02_prompt0_option02                                                                                                                                                                                                                                                                                                          NaN  
simplify task                                                                                                                                                                                                                                                                                 Make the language appropriate for a lay audience  
simple_summary02_prompt1_option01  Exercise snacks may be the solution to improving our health and fitness levels. Exercise snacks are short bursts of vigorous exercise that can be done multiple times throughout the day. A study showed that three bouts of climbing stairs for 20 seconds improved cardiorespiratory fitness (CRF) by ...  
simple_summary02_prompt1_option02  Exercise Snacks are a new way to improve your health through brief periods of intense exercise. Studies have shown that even short bursts of vigorous activity can improve your cardiovascular fitness and reduce the negative effects of sitting for long periods of time. Inactive adults who particip...

In [110]:
qna_dict[iteration_id][0]

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, can improve cardiometabolic health and exercise performance in inactive adults, according to recent studies. These snacks involve thrice daily 15-30 seconds of hard effort involving cycling or practical stair climbing, making them a feasible exercise strategy. Further research is needed to establish their efficacy in clinical populations and determine their applicability in a real-world setting. This emerging evidence highlights the potential of exercise snacks to mitigate the impact of sedentary lifestyles on cardiometabolic health.',
  'Exercise snacks are a novel strateg

In [107]:
qna_dict[iteration_id]

[{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, can improve cardiometabolic health and exercise performance in inactive adults, according to recent studies. These snacks involve thrice daily 15-30 seconds of hard effort involving cycling or practical stair climbing, making them a feasible exercise strategy. Further research is needed to establish their efficacy in clinical populations and determine their applicability in a real-world setting. This emerging evidence highlights the potential of exercise snacks to mitigate the impact of sedentary lifestyles on cardiometabolic health.',
   'Exercise snacks are a novel 

## 3.7

In [114]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simple_summary_dict[simplify_iteration] = self.qna
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            # new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            new_key = re.sub(self.response_regex, rf'simple_summary\1', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                response_dict = dict()
                for index, choice in enumerate(response.choices):
                    response_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
                # response_dict['simplify task'] = simplify_task
                self.simple_summary_dict[simplify_iteration] = response_dict

            except:
                self.simple_summary_dict[simplify_iteration][new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        # self.qna.setdefault(f'simple summary', [])
        # self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[simplify_iteration].values()])
        # self.qna[f'simple summary'] = self.simple_summary_dict[simplify_iteration]
        for key, value in self.simple_summary_dict[simplify_iteration].items():
            self.qna.setdefault(key, []) # key refers to new_key_option{n}
            self.qna[key].extend([value])
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(data) for data in simple_summaries_master_list
        ])
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to create results DataFrame')
        
        qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    if save_outputs:
        try:
            save_output(
                qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                csv_path=csv_path, pickle_path=pickle_path)
            save_output(
                chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                csv_path=None, pickle_path=pickle_path)
        except:
            print('[prompt_chaining_dict()] Unable to save outputs')
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 3.7
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [115]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3.7
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [119]:
qna_dict[iteration_id][0].keys()

dict_keys(['article_title', 'system_role', 'model', 'prep step', 'summarization task', 'summary', 'simple_summary02_option01', 'simple_summary02_option02', 'simplify task', 'text'])

In [118]:
qna_dict[iteration_id][0]['simple_summary02_option02']

["Exercise Snacks are a new and innovative approach to improving our health. This involves doing small bouts of intense exercise throughout the day, instead of one long session. The goal is to improve our cardiovascular fitness and metabolic health, especially for those who are inactive or at risk for chronic diseases. Studies have shown that even short bursts of exercise can make a significant impact on our health. Exercise Snacks can be done at home or work, and involve activities like stair climbing or cycling. These exercises are easy to do and don't require any special equipment. Exercise Snacks are a practical and effective way to improve our health and reduce the impact of sedentary lifestyles.",
 "Exercise snacks are a new and trendy way to improve your heart health. They are short bursts of exercise that you can do throughout the day, even during work breaks. Researchers have found that just a few minutes of intense exercise, like climbing stairs or cycling, can boost your fit

In [122]:
chatbot_dict[iteration_id]['text1_prompt00'].simple_summary_dict

{0: {'simple_summary02_option01': 'Exercise Snacks, a term coined for brief bouts of exercise performed multiple times throughout the day, could be an effective strategy to improve heart health. Studies show that vigorous exercise snacks, involving short bursts of cycling or stair climbing, can improve cardiorespiratory fitness and exercise performance in inactive adults. These exercise snacks can also reduce the negative effects of sedentary behavior on metabolic health. Exercise snacks are easy to incorporate into daily life, and their benefits do not require all-out efforts or specialized equipment. While more research is needed to establish their efficacy in clinical populations, exercise snacks align with the updated Physical Activity Guidelines and the WHO Guidelines on Physical Activity and Sedentary Behavior.',
  'simple_summary02_option02': "Exercise Snacks are a new and innovative approach to improving our health. This involves doing small bouts of intense exercise throughout

### Getting close

In [124]:
pd.DataFrame(qna_dict[iteration_id][3])

article_title  \
0  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

                                                     summarization task  \
0  Describe the interesting points to your coworker at the water cooler   
1  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
0  Hey, have you heard of exercise snacks? It's a new strategy to improve cardiometabolic health by performing isolated bouts of brief vigorous exercise multiple times throughout the day. Studies have shown that exercise snacks involving cycling or stair climbing can improve cardiorespiratory fitne...   
1  Hey, have you heard about exercise snacks? It's a new strategy for improving cardiovascular and metabolic health. Basically, it involves performing isolated bouts of brief vigorous exercise multiple times throughout the day. And the best part is, you don't need to spend hours at the gym to reap ...   

                                                                                                                                                                                                                                                                                     simple_summary02_option01  \
0  Exercise snacks are a new and interesting way to improve our health. They are short bursts of exercise that can be done throughout the day, even at work or home. These exercises can be done quickly and involve things like climbing stairs or doing jumping jacks. They have been shown to improve ou...   
1  Exercise Snacks are a new and innovative way to improve your heart and metabolic health. Exercise Snacks involve doing short bursts of intense exercise throughout the day, rather than one long workout. Studies have shown that even just three daily bouts of vigorous stair climbing, each lasting j...   

                                                                                                                                                                                                                                                                                     simple_summary02_option02  \
0  Exercise snacks, which are brief and intense bouts of exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving cycling or stair climbing can improve cardiovascular fitness and exercise ...   
1                                                                                                                                                                                                                   Do you want me to simplify the entire article or just provide a summary in layman's terms?   

                                      simplify task  \
0  Make the language appropriate for a lay audience   
1  Make the language appropriate for a lay audience   

                                                                                                                                                                                                                                                                                                          text  
0  Exercise Snacks A

In [121]:

pd.DataFrame(qna_dict[iteration_id][0])

article_title  \
0  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

              summarization task  \
0  Summarize for a LinkedIn post   
1  Summarize for a LinkedIn post   

                                                                                                                                                                                                                                                                                                       summary  \
0  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible exercise strategy to improve cardiometabolic health. Recent studies have shown that exercise snacks involving thrice daily ~1530 s of hard effort involving cyclin...   
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling and ...   

                                                                                                                                                                                                                                                                                     simple_summary02_option01  \
0  Exercise Snacks, a term coined for brief bouts of exercise performed multiple times throughout the day, could be an effective strategy to improve heart health. Studies show that vigorous exercise snacks, involving short bursts of cycling or stair climbing, can improve cardiorespiratory fitness a...   
1  Exercise snacks are short bursts of vigorous exercise that can be performed multiple times throughout the day. They are a feasible way to improve cardiometabolic health and reduce the impact of sedentary behavior. Exercise snacks involve brief periods of intense activity, such as cycling or stai...   

                                                                                                                                                                                                                                                                                     simple_summary02_option02  \
0  Exercise Snacks are a new and innovative approach to improving our health. This involves doing small bouts of intense exercise throughout the day, instead of one long session. The goal is to improve our cardiovascular fitness and metabolic health, especially for those who are inactive or at risk...   
1  Exercise snacks are a new and trendy way to improve your heart health. They are short bursts of exercise that you can do throughout the day, even during work breaks. Researchers have found that just a few minutes of intense exercise, like climbing stairs or cycling, can boost your fitness levels...   

                                      simplify task  \
0  Make the language appropriate for a lay audience   
1  Make the language appropriate for a lay audience   

                                                                                                                                                                                                                                                                                                          text  
0  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health\n\nTHE EFFICACY OF EXERCISE SNACKS FOR IMPROVING CRF IN INACTIVE AD

In [116]:
qna_dict[iteration_id]

[{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible exercise strategy to improve cardiometabolic health. Recent studies have shown that exercise snacks involving thrice daily ~15\x9630 s of hard effort involving cycling and more practical stair climbing are efficacious for improving CRF and exercise performance in inactive adults. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity, but their efficacy in clinical populations remains to be established.',
   'Exercise snacks, defined as isolated bouts of brief vigorous exercise perfor

## 3.8

In [125]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simple_summary_dict[simplify_iteration] = self.qna
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            # new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            new_key = re.sub(self.response_regex, rf'simple_summary\1', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    simple_summary_option = f'{new_key}_option{"{:02d}".format(index+1)}'
                    self.simple_summary_dict[simplify_iteration].setdefault(simple_summary_option, {})
                    self.simple_summary_dict[simplify_iteration][simple_summary_option] = choice["message"]["content"]                    
                    print(f'\t...Summary given')

            except:
                self.simple_summary_dict[simplify_iteration][new_key] = self.simplify_bot_dict[new_key].gpt(simplify_prompt)
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        # self.qna.setdefault(f'simple summary', [])
        # self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[simplify_iteration].values()])
        # self.qna[f'simple summary'] = self.simple_summary_dict[simplify_iteration]
        for key, value in self.simple_summary_dict[simplify_iteration].items():
            self.qna.setdefault(key, []) # key refers to new_key_option{n}
            self.qna[key].extend([value])
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(data) for data in simple_summaries_master_list
        ])
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to create results DataFrame')
        
        qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    if save_outputs:
        try:
            save_output(
                qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                csv_path=csv_path, pickle_path=pickle_path)
            save_output(
                chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                csv_path=None, pickle_path=pickle_path)
        except:
            print('[prompt_chaining_dict()] Unable to save outputs')
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 3.8
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [127]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3.8
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3


AttributeError: 'Chaining' object has no attribute 'simplify_bot_dict'

## 3.9

In [130]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simple_summary_dict[simplify_iteration] = self.qna
        self.simple_summary_dict[simplify_iteration] = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            # new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            new_key = re.sub(self.response_regex, rf'simple_summary\1', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    simple_summary_option = f'{new_key}_option{"{:02d}".format(index+1)}'
                    self.simple_summary_dict[simplify_iteration].setdefault(simple_summary_option, {})
                    self.simple_summary_dict[simplify_iteration][simple_summary_option] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                self.simple_summary_dict[simplify_iteration][new_key] = response
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        # self.qna.setdefault(f'simple summary', [])
        # self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[simplify_iteration].values()])
        # self.qna[f'simple summary'] = self.simple_summary_dict[simplify_iteration]
        for key, value in self.simple_summary_dict[simplify_iteration].items():
            self.qna.setdefault(key, []) # key refers to new_key_option{n}
            self.qna[key].extend([value])
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(data) for data in simple_summaries_master_list
        ])
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to create results DataFrame')
        
        qna_chain_dict[iteration_id+0.001] = simple_summaries_master_list
    if save_outputs:
        try:
            save_output(
                qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                csv_path=csv_path, pickle_path=pickle_path)
            save_output(
                chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                csv_path=None, pickle_path=pickle_path)
        except:
            print('[prompt_chaining_dict()] Unable to save outputs')
    qna_chain_dict[iteration_id] = simple_summaries_master_list
    return qna_chain_dict


iteration_id = 3.9
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 1.4
pause_per_request=20
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 20 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [131]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3.9
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [136]:
pd.DataFrame(qna_dict[iteration_id][0])

article_title  \
0  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

              summarization task  \
0  Summarize for a LinkedIn post   
1  Summarize for a LinkedIn post   

                                                                                                                                                                                                                                                                                                       summary  \
0  Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks involving cycling or practical stair climbing are efficacious for improving cardiorespirator...   
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardio-metabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~1530 s of hard effort involving cycling and...   

                                                                                                                                                                                                                                                                                     simple_summary01_option01  \
0  Exercise snacks are brief bouts of vigorous exercise performed multiple times throughout the day. They are a new and innovative strategy to improve our health. These snacks can be easily incorporated into our daily routine, such as taking the stairs instead of the elevator or doing jumping jacks...   
1  "Exercise Snacks: A Novel Way to Improve Health"\n\nAre you looking for a new way to improve your health? Exercise snacks might be just what you need! Exercise snacks are short bursts of intense exercise that you can do throughout the day. They are a convenient and effective way to improve your ...   

                                                                                                                                                                                                                                                                                     simple_summary01_option02  \
0  Exercise Snacks is a new approach to improving heart health and overall fitness. It involves short, intense bursts of exercise throughout the day, rather than one long workout. Studies have shown that even small amounts of exercise can have significant benefits, such as improving cardiovascular ...   
1  Exercise Snacks: A Quick and Easy Way to Improve Your Health\n\nDo you struggle to find time to exercise? Do you feel like you're not doing enough to improve your health? Exercise snacks might be the solution for you. Exercise snacks are short bursts of intense exercise that you can fit into you...   

                                                                                                                                                                                                                                                                                     simple_summary02_option01  \
0  Exercise snacks are a new approach to improve our heart and metabolic health. They involve doing short bursts of exercise throughout the day, rather than one long session. Studies have shown that even just a few minutes of intense exercise, like climbing stairs or cycling, can improve our fitnes...

### Getting close

In [137]:
print(pd.concat([pd.DataFrame(value) for value in qna_dict[iteration_id]]).shape)
pd.concat([pd.DataFrame(value) for value in qna_dict[iteration_id]])

(16, 12)


article_title  \
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

                                                     summarization task  \
0                                         Summarize for a LinkedIn post   
1             

In [132]:
qna_dict[iteration_id]

[{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks involving cycling or practical stair climbing are efficacious for improving cardiorespiratory fitness, exercise performance, and metabolic health in inactive adults. They may also have potential to improve vascular health, although more research is needed. Exercise snacks align with the recently revised Physical Activity Guidelines for Americans and the World Health Organization, which eliminated the previous requirement that physical activity had to be accumulated in bou

# Iteration 4

In [139]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        # self.simple_summary_dict[simplify_iteration] = self.qna
        self.simple_summary_dict[simplify_iteration] = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            # new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            new_key = re.sub(self.response_regex, rf'simple_summary\1', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    simple_summary_option = f'{new_key}_option{"{:02d}".format(index+1)}'
                    self.simple_summary_dict[simplify_iteration].setdefault(simple_summary_option, {})
                    self.simple_summary_dict[simplify_iteration][simple_summary_option] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                self.simple_summary_dict[simplify_iteration][new_key] = response
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # self.simple_summary_dict['simplify_task'] = simplify_task
        # self.qna.setdefault(f'simple summary', [])
        # self.qna[f'simple summary'].extend([value for value in self.simple_summary_dict[simplify_iteration].values()])
        # self.qna[f'simple summary'] = self.simple_summary_dict[simplify_iteration]
        for key, value in self.simple_summary_dict[simplify_iteration].items():
            self.qna.setdefault(key, []) # key refers to new_key_option{n}
            self.qna[key].extend([value])
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        # self.qna[f'simple summary {new_key}'].extend([value for value in self.simple_summary_dict.values()])
        # self.qna['simple summary'] = dict()
        # self.qna['simple summary'][simplify_iteration] = [value for value in self.simple_summary_dict.values()]
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(data) for data in simple_summaries_master_list
        ])
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to create results DataFrame')
        
        qna_chain_dict[iteration_id] = simple_summaries_master_list
    if save_outputs:
        try:
            save_output(
                qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                csv_path=csv_path, pickle_path=pickle_path)
            save_output(
                chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                csv_path=None, pickle_path=pickle_path)
        except:
            print('[prompt_chaining_dict()] Unable to save outputs')
    return qna_chain_dict


iteration_id = 4
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

# summary_iteration_id = iteration_id
summary_iteration_id = 3.9
pause_per_request=20
# relevance_prompts = relevance_prompts_df

# qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
#     n_choices=n_choices, pause_per_request=pause_per_request,
#     iteration_id=iteration_id)

qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3.9
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [142]:
pd.DataFrame(qna_dict[iteration_id][0])

ValueError: All arrays must be of the same length

In [143]:
qna_dict[iteration_id][0]

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks involving cycling or practical stair climbing are efficacious for improving cardiorespiratory fitness, exercise performance, and metabolic health in inactive adults. They may also have potential to improve vascular health, although more research is needed. Exercise snacks align with the recently revised Physical Activity Guidelines for Americans and the World Health Organization, which eliminated the previous requirement that physical activity had to be accumulated in bouts las

In [140]:
qna_dict[iteration_id]

[{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
  'system_role': 'You are an expert at science communication.',
  'model': 'gpt-3.5-turbo',
  'prep step': 'Take the key points and numerical descriptors to',
  'summarization task': 'Summarize for a LinkedIn post',
  'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks involving cycling or practical stair climbing are efficacious for improving cardiorespiratory fitness, exercise performance, and metabolic health in inactive adults. They may also have potential to improve vascular health, although more research is needed. Exercise snacks align with the recently revised Physical Activity Guidelines for Americans and the World Health Organization, which eliminated the previous requirement that physical activity had to be accumulated in bou

## 4.1

In [ ]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simple_summary_dict[simplify_iteration] = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            # new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            new_key = re.sub(self.response_regex, rf'simple_summary\1', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    simple_summary_option = f'{new_key}_option{"{:02d}".format(index+1)}'
                    self.simple_summary_dict[simplify_iteration].setdefault(simple_summary_option, {})
                    self.simple_summary_dict[simplify_iteration][simple_summary_option] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                self.simple_summary_dict[simplify_iteration][new_key] = response
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
        for key, value in self.simple_summary_dict[simplify_iteration].items():
            self.qna.setdefault(key, []) # key refers to new_key_option{n}
            self.qna[key].extend([value])
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(data) for data in simple_summaries_master_list
        ])
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to create results DataFrame')
        
        qna_chain_dict[iteration_id] = simple_summaries_master_list
    if save_outputs:
        try:
            save_output(
                qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                csv_path=csv_path, pickle_path=pickle_path)
            save_output(
                chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                csv_path=None, pickle_path=pickle_path)
        except:
            print('[prompt_chaining_dict()] Unable to save outputs')
    return qna_chain_dict


iteration_id = 4
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

# summary_iteration_id = iteration_id
summary_iteration_id = 3.9
pause_per_request=18
# relevance_prompts = relevance_prompts_df

# qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
#     n_choices=n_choices, pause_per_request=pause_per_request,
#     iteration_id=iteration_id)

qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 3.9
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 20 sec to avoid exceeding API rate limit
		...Prepar

In [146]:
chatbot_dict[summary_iteration_id]['text1_prompt00'].qna

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': ['Exercise snacks, defined as brief bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks involving cycling or practical stair climbing are efficacious for improving cardiorespiratory fitness, exercise performance, and metabolic health in inactive adults. They may also have potential to improve vascular health, although more research is needed. Exercise snacks align with the recently revised Physical Activity Guidelines for Americans and the World Health Organization, which eliminated the previous requirement that physical activity had to be accumulated in bouts las

## 4.2

In [147]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simple_summary_dict[simplify_iteration] = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            # new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            new_key = re.sub(self.response_regex, rf'simple_summary\1', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    simple_summary_option = f'{new_key}_option{"{:02d}".format(index+1)}'
                    self.simple_summary_dict[simplify_iteration].setdefault(simple_summary_option, {})
                    self.simple_summary_dict[simplify_iteration][simple_summary_option] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                self.simple_summary_dict[simplify_iteration][new_key] = response
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        for key, value in self.simple_summary_dict[simplify_iteration].items():
            self.qna.setdefault(key, []) # key refers to new_key_option{n}
            self.qna[key].extend([value])
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(data) for data in simple_summaries_master_list
        ])
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to create results DataFrame')
        
        qna_chain_dict[iteration_id] = simple_summaries_master_list
    if save_outputs:
        try:
            save_output(
                qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                csv_path=csv_path, pickle_path=pickle_path)
            save_output(
                chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                csv_path=None, pickle_path=pickle_path)
        except:
            print('[prompt_chaining_dict()] Unable to save outputs')
    return qna_chain_dict


iteration_id = 4.2
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 3.9
pause_per_request=18
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [148]:
qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [149]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving thrice daily ~15-30 seconds of hard effort involving cycling and mo...   
2  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible exercise strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~1530 s of hard effort involving cycli...   
1  Hey, have you heard of exercise snacks? It's a new strategy to improve cardiometabolic health by performing isolated bouts of brief vigorous exercise multiple times throughout the day! Studies have shown that these exercise snacks can improve CRF and exercise performance in inactive adults. And ...   
2  Hey! Have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health. Basically, 

In [155]:
simplify_prompts

['Assume your audience has no science background.',
 'Make the language appropriate for a lay audience']

In [151]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 4.2
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 18 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 18 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 18 sec to avoid exceeding API rate limit
		...Prepar

In [154]:
chatbot_dict[summary_iteration_id]['text1_prompt00'].qna

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': ['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving thrice daily ~15-30 seconds of hard effort involving cycling and more practical stair climbing are efficacious for improving CRF and exercise performance in inactive adults. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity, but their efficacy in clinical populations remains to be established. The applicability of exercise snacks in a real-world setting and the potential for exercise snacks 

### Results
Not quite right

In [157]:
qna_dict[iteration_id]['summary'].unique()

array(['Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving thrice daily ~15-30 seconds of hard effort involving cycling and more practical stair climbing are efficacious for improving CRF and exercise performance in inactive adults. Exercise snacks may also have potential to improve aspects of cardiometabolic health in individuals with obesity, but their efficacy in clinical populations remains to be established. The applicability of exercise snacks in a real-world setting and the potential for exercise snacks to target musculoskeletal health are yet to be determined.',
       'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible exercise strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks inv

In [163]:
qna_dict[iteration_id]['simple_summary02_option02'].unique()

array(['Exercise Snacks is a new strategy to improve our health. This strategy involves doing short bursts of vigorous exercise throughout the day. According to some studies, this approach can improve our cardiovascular fitness and exercise performance. The exercise snacks can involve different types of exercises such as cycling or climbing stairs. This strategy can also be helpful for people who have a sedentary lifestyle or are at risk of developing cardiometabolic diseases. Although more research is needed to fully understand the benefits of exercise snacks, this approach can be an easy way to incorporate exercise into our daily routine.',
       'Exercise snacks are a new and innovative way to improve your heart and metabolic health. They involve short bursts of intense exercise, such as climbing stairs or cycling, performed several times throughout the day. Studies have shown that exercise snacks can improve cardiovascular fitness and exercise performance, even in previously inact

In [162]:
qna_dict[iteration_id]['simple_summary02_option02']

0    Exercise Snacks is a new strategy to improve our health. This strategy involves doing short bursts of vigorous exercise throughout the day. According to some studies, this approach can improve our cardiovascular fitness and exercise performance. The exercise snacks can involve different types of...
1    Exercise snacks are a new and innovative way to improve your heart and metabolic health. They involve short bursts of intense exercise, such as climbing stairs or cycling, performed several times throughout the day. Studies have shown that exercise snacks can improve cardiovascular fitness and e...
0    Exercise Snacks is a new strategy to improve our health. This strategy involves doing short bursts of vigorous exercise throughout the day. According to some studies, this approach can improve our cardiovascular fitness and exercise performance. The exercise snacks can involve different types of...
1    Exercise snacks are a new and innovative way to improve your heart and metabolic

In [158]:
qna_dict[iteration_id]['summary']

0    Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving thrice daily ~15-30 seconds of hard effort involving cycling and mo...
1    Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible exercise strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~1530 s of hard effort involving cycli...
0    Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies have shown that exercise snacks involving thrice daily ~15-30 seconds of hard effort involving cycling and mo...
1    Exercise snacks, defined as isolated bouts of brief vigorous exercise performed 

In [153]:
print(qna_dict[iteration_id].shape)
print(qna_dict[iteration_id].columns)
print(qna_dict[iteration_id].index)
qna_dict[iteration_id]

(16, 12)
Index(['article_title', 'system_role', 'model', 'prep step',
       'summarization task', 'summary', 'simple_summary01_option01',
       'simple_summary01_option02', 'simple_summary02_option01',
       'simple_summary02_option02', 'simplify task', 'text'],
      dtype='object')
Int64Index([0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1], dtype='int64')


article_title  \
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

                                                     summarization task  \
0                                         Summarize for a LinkedIn post   
1             

## 4.3

In [164]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simple_summary_dict[simplify_iteration] = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            # new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            new_key = re.sub(self.response_regex, rf'simple_summary\1', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    simple_summary_option = f'{new_key}_option{"{:02d}".format(index+1)}'
                    self.simple_summary_dict[simplify_iteration].setdefault(simple_summary_option, {})
                    self.simple_summary_dict[simplify_iteration][simple_summary_option] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                self.simple_summary_dict[simplify_iteration][new_key] = response
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        for key, value in self.simple_summary_dict[simplify_iteration].items():
            self.qna[key] = value
        self.qna['simplify task'] = simplify_task
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, qna_chain_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            # summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(data) for data in simple_summaries_master_list
        ])
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        print('Unable to create results DataFrame')
        
        qna_chain_dict[iteration_id] = simple_summaries_master_list
    if save_outputs:
        try:
            save_output(
                qna_chain_dict[iteration_id], description='prompt_chain_experiment',
                csv_path=csv_path, pickle_path=pickle_path)
            save_output(
                chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                csv_path=None, pickle_path=pickle_path)
        except:
            print('[prompt_chaining_dict()] Unable to save outputs')
    return qna_chain_dict


iteration_id = 4.3
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 3.9
pause_per_request=18
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

In [165]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, which are defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. This emerging concept involves short and intense bursts of exercise that can be easily incorporated into da...   
2  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible and effective strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~15-30 s of hard effort involving ...   
1  Hey! Have you heard about exercise snacks? It's a new approach to improve cardiometabolic health by performing brief and isolated bouts of vigorous exercise throughout the day. The studies have shown that it is effective in improving cardiorespiratory fitness and indices of exercise performance ...   
2  Hey! Have you heard of exercise snacks? They are brief bouts of vigorous exercise that you can do multiple ti

In [166]:
qna_dict = prompt_chaining_dict(simplify_prompts, qna_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 4.3
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 18 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 18 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 18 sec to avoid exceeding API rate limit
		...Prepar

In [169]:
chatbot_dict[summary_iteration_id]['text1_prompt00'].qna

{'article_title': 'Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health',
 'system_role': 'You are an expert at science communication.',
 'model': 'gpt-3.5-turbo',
 'prep step': 'Take the key points and numerical descriptors to',
 'summarization task': 'Summarize for a LinkedIn post',
 'summary': ['Exercise snacks, which are defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. This emerging concept involves short and intense bursts of exercise that can be easily incorporated into daily activities, such as stair climbing or jumping jacks during a break between virtual meetings. Recent studies have shown that exercise snacks can improve cardiovascular fitness, exercise performance, and metabolic outcomes in previously inactive adults and individuals with obesity. While the applicability of exercise snacks in a real-world setting and their potential to target musculos

In [178]:
chatbot_dict[summary_iteration_id]['text1_prompt00'].simple_summary_dict

{0: {'simple_summary01_option01': 'Exercise snacks are a new and easy way to improve our health. They involve performing brief but intense exercise routines multiple times throughout the day. Studies have shown that exercise snacks can improve our cardiovascular fitness, which is an important measure of our heart and lung health. These brief exercise routines can be done using different activities such as cycling or stair climbing, and they can be done at home, school, or work. Exercise snacks are especially beneficial for people who are not physically active or who have health conditions that make traditional exercise challenging. They are easy to incorporate into our daily routines and can help break up periods of sitting, which can be harmful to our health.',
  'simple_summary01_option02': 'Exercise snacks are short bursts of vigorous exercise that can be performed throughout the day. These snacks can be a quick set of stair climbs or cycling sprints that last only a few seconds, fo

In [180]:
pd.DataFrame(chatbot_dict[summary_iteration_id]['text1_prompt00'].simple_summary_dict).transpose()

simple_summary01_option01  \
0  Exercise snacks are a new and easy way to improve our health. They involve performing brief but intense exercise routines multiple times throughout the day. Studies have shown that exercise snacks can improve our cardiovascular fitness, which is an important measure of our heart and lung health....   
1  Exercise snacks are a new and exciting way to improve heart and metabolic health. They involve short bursts of vigorous exercise throughout the day, rather than one long session. Studies have shown that exercise snacks can improve cardiorespiratory fitness (CRF) and exercise performance in inact...   

                                                                                                                                                                                                                                                                                     simple_summary01_option02  \
0  Exercise snacks are short bursts of vigorous exercise that can be performed throughout the day. These snacks can be a quick set of stair climbs or cycling sprints that last only a few seconds, followed by a cooldown period. The idea is to perform these exercise snacks multiple times a day to imp...   
1  Exercise Snacks are a new and effective way to improve heart and metabolic health. These quick bursts of exercise involve performing brief, intense workouts throughout the day. Studies have shown that just a few minutes of vigorous exercise, like climbing stairs or cycling, can significantly imp...   

                                                                                                                                                                                                                                                                                     simple_summary02_option01  \
0  Exercise snacks are short bursts of intense physical activity that can be done multiple times throughout the day. These can include activities like climbing stairs or doing jumping jacks for a brief period of time. Research has shown that exercise snacks can improve cardiovascular fitness and ex...   
1  Exercise Snacks: A New Way to Improve Your Health\n\nAre you looking for a way to improve your health but don't have a lot of time for exercise? Exercise snacks might be the solution for you! Exercise snacks are short bursts of vigorous exercise that can be performed multiple times throughout th...   

                                                                                                                                                                                                                                                                                     simple_summary02_option02  \
0  Exercise snacks are short bursts of exercise that can be done throughout the day to improve health. Studies have shown that even brief periods of intense exercise, like climbing stairs quickly or doing jumping jacks, can improve heart and lung function, as well as reduce the negative effects of ...   
1  Exercise snacks are a new way to improve your health through short bursts of exercise throughout the day. Studies have shown that even just a few minutes of vigorous exercise, like climbing stairs or cycling, can improve your cardiovascular fitness and help reduce the negative effects of sitting...   

                                      simplify task  
0   Assume your audience has no science background.  
1  Make the language appropriate for a lay audience

In [182]:
pd.DataFrame(chatbot_dict[summary_iteration_id]['text1_prompt00'].qna)

article_title  \
0  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

              summarization task  \
0  Summarize for a LinkedIn post   
1  Summarize for a LinkedIn post   

                                                                                                                                                                                                                                                                                                       summary  \
0  Exercise snacks, which are defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. This emerging concept involves short and intense bursts of exercise that can be easily incorporated into da...   
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible and effective strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~15-30 s of hard effort involving ...   

                                                                                                                                                                                                                                                                                     simple_summary01_option01  \
0  Exercise snacks are a new and exciting way to improve heart and metabolic health. They involve short bursts of vigorous exercise throughout the day, rather than one long session. Studies have shown that exercise snacks can improve cardiorespiratory fitness (CRF) and exercise performance in inact...   
1  Exercise snacks are a new and exciting way to improve heart and metabolic health. They involve short bursts of vigorous exercise throughout the day, rather than one long session. Studies have shown that exercise snacks can improve cardiorespiratory fitness (CRF) and exercise performance in inact...   

                                                                                                                                                                                                                                                                                     simple_summary01_option02  \
0  Exercise Snacks are a new and effective way to improve heart and metabolic health. These quick bursts of exercise involve performing brief, intense workouts throughout the day. Studies have shown that just a few minutes of vigorous exercise, like climbing stairs or cycling, can significantly imp...   
1  Exercise Snacks are a new and effective way to improve heart and metabolic health. These quick bursts of exercise involve performing brief, intense workouts throughout the day. Studies have shown that just a few minutes of vigorous exercise, like climbing stairs or cycling, can significantly imp...   

                                                                                                                                                                                                                                                                                     simple_summary02_option01  \
0  Exercise Snacks: A New Way to Improve Your Health\n\nAre you looking for a way to improve your health but don't have a lot of time for exercise? Exercise snacks might be the solution for you! Exercise snacks are short bursts of vigorous exercise that can be performed multiple times throughout th...

In [170]:
qna_dict[iteration_id]['simple_summary01_option01'].unique()

array(['Exercise snacks are a new and exciting way to improve heart and metabolic health. They involve short bursts of vigorous exercise throughout the day, rather than one long session. Studies have shown that exercise snacks can improve cardiorespiratory fitness (CRF) and exercise performance in inactive adults. For example, climbing three flights of stairs as quickly as possible, with a warm-up and cool-down, three times a day, three times a week for six weeks, improved CRF by 5% and peak power output by 12%. Exercise snacks can also benefit people with obesity, by reducing insulin and nonesterified fatty acids in the blood. These snacks are easy to perform, such as doing jumping jacks, air squats or lunges. Exercise snacks can be done at home or work and can help break up long periods of sitting, which can be harmful to our health. More research is needed to fully understand their benefits, but exercise snacks offer a practical and effective way to improve our health.',
       "Exe

In [171]:
qna_dict[iteration_id]['simple_summary01_option01']

0    Exercise snacks are a new and exciting way to improve heart and metabolic health. They involve short bursts of vigorous exercise throughout the day, rather than one long session. Studies have shown that exercise snacks can improve cardiorespiratory fitness (CRF) and exercise performance in inact...
1    Exercise snacks are a new and exciting way to improve heart and metabolic health. They involve short bursts of vigorous exercise throughout the day, rather than one long session. Studies have shown that exercise snacks can improve cardiorespiratory fitness (CRF) and exercise performance in inact...
0    Exercise snacks are a new and exciting way to improve heart and metabolic health. They involve short bursts of vigorous exercise throughout the day, rather than one long session. Studies have shown that exercise snacks can improve cardiorespiratory fitness (CRF) and exercise performance in inact...
1    Exercise snacks are a new and exciting way to improve heart and metabolic health

In [173]:
qna_dict[iteration_id]['summary'].unique()

array(['Exercise snacks, which are defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. This emerging concept involves short and intense bursts of exercise that can be easily incorporated into daily activities, such as stair climbing or jumping jacks during a break between virtual meetings. Recent studies have shown that exercise snacks can improve cardiovascular fitness, exercise performance, and metabolic outcomes in previously inactive adults and individuals with obesity. While the applicability of exercise snacks in a real-world setting and their potential to target musculoskeletal health remain to be determined, this novel strategy has the potential to encourage more people to engage in regular physical activity.',
       'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible and effective strate

In [177]:
print(qna_dict[iteration_id].drop_duplicates(inplace=False).shape)
qna_dict[iteration_id].drop_duplicates(inplace=False)

(8, 12)


article_title  \
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

                                                     summarization task  \
0                                         Summarize for a LinkedIn post   
1                                         Summarize for a LinkedIn post   
0  Describe the interesting points to your coworker at the water cooler   
1  Describe the interesting points to your coworker at the water cooler   
0                                         Summarize for a LinkedIn post   
1                                         Summarize for a LinkedIn post   
0  Describe the interesting points to your coworker at the water cooler   
1  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
0  Exercise snacks, which are defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. This emerging concept involves short and intense bursts of exercise that can be easily incorporated into da...   
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible and effective strategy to improve cardiometabolic health. Emerging evidence suggests that exercise snacks involving thrice daily ~15-30 s of hard effort involving ...   
0  Hey! Have you heard about exercise snacks? It's a new approach to improve cardiometabolic health by performing brief and isolated bouts of vigorous exercise throughout the day. The studies have shown that it is effective in improving cardiorespiratory fitness and indices of exercise performance ...   
1  Hey! Have you heard of exercise snacks? They are brief bouts of vigorous exercise that you can do multiple ti

In [168]:
print(qna_dict[iteration_id].shape)
print(qna_dict[iteration_id].columns)
print(qna_dict[iteration_id].index)
qna_dict[iteration_id]

(16, 12)
Index(['article_title', 'system_role', 'model', 'prep step',
       'summarization task', 'summary', 'simple_summary01_option01',
       'simple_summary01_option02', 'simple_summary02_option01',
       'simple_summary02_option02', 'simplify task', 'text'],
      dtype='object')
Int64Index([0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1], dtype='int64')


article_title  \
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
0  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
0  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
0  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   

                                                     summarization task  \
0                                         Summarize for a LinkedIn post   
1             

# Iteration 5

In [184]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simple_summary_dict[simplify_iteration] = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            # new_key = re.sub(self.response_regex, rf'simple_summary\1_prompt{str(simplify_iteration)}', key)
            new_key = re.sub(self.response_regex, rf'simple_summary\1', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            # self.simple_summary_dict[f'{simplify_iteration}'] = simplify_task
            # self.qna.setdefault('simplify task', [])
            # self.qna['simplify task'].extend(simplify_task)

            # self.qna[f'simplify task {new_key}'] = simplify_task
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    simple_summary_option = f'{new_key}_option{"{:02d}".format(index+1)}'
                    self.simple_summary_dict[simplify_iteration].setdefault(simple_summary_option, {})
                    self.simple_summary_dict[simplify_iteration][simple_summary_option] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                self.simple_summary_dict[simplify_iteration][new_key] = response
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        # for key, value in self.simple_summary_dict[simplify_iteration].items():
        #     self.qna[key] = value
        # self.qna['simplify task'] = simplify_task
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        # try:
        #     self.qna.update({'text': self.qna.pop('text')})
        # except:
        #     pass
        # return self.qna
        return self.simple_summary_dict
    
    def add_relevance(self, task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    relevance_iteration=None, pause_per_request=20
                    ):
        self.relevance_bot_dict = dict()
        self.relevance_dict = dict()
        if relevance_iteration == None:
            relevance_iteration = 1
        for key, summary in self.summaries_dict.items():
            new_key = re.sub(self.response_regex, rf'relevance\1_prompt{str(relevance_iteration)}', key)
            print(f'\t\t...Preparing to summarize {key}')
            self.relevance_bot_dict[new_key] = Chaining(
                summary, system_role=system_role,
                model=model, temperature=temperature, n_choices=n_choices, max_tokens=max_tokens
                )
            relevance_prompt = self.relevance_bot_dict[new_key].create_prompt(task)
            try:
                response = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.add_relevance()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    self.relevance_dict[f'{new_key}_option{"{:02d}".format(index+1)}'] = choice["message"]["content"]
                    print(f'\t...Relevance given')
            except:
                try:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt).choices[0]["message"]["content"]
                    print(f'\t...First relevance response given')
                except:
                    self.relevance_dict[new_key] = self.relevance_bot_dict[new_key].gpt(relevance_prompt)
                    print(f'\t...Error parsing response for added relevance request')
            print(f'[.add_relevance()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.relevance_dict[f'relevance_task{"{:02d}".format(relevance_iteration)}'] = task
        self.qna.setdefault('added relevance', [])
        self.qna['added relevance'].extend([value for value in self.relevance_dict.values])
        try:
            self.qna.update({'text': self.qna.pop('text')})
        except:
            pass
        return self.qna

def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, simple_summaries_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_dict = dict()
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        # simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            # summary_dict[f'{prompt_column} task'] = prompt
            simple_summaries_master_list.append(summary_dict)
        #     simple_summaries_master_dict[text_prompt_key][index] = summary_dict
        # simple_summaries_master_list.append(simple_summaries_master_dict[text_prompt_key])
    # try:
    #     qna_dict[iteration_id] = pd.concat([
    #         pd.DataFrame(data) for data in simple_summaries_master_list
    #     ])
    # except Exception as error:
    #     exc_type, exc_obj, tb = sys.exc_info()
    #     f = tb.tb_frame
    #     lineno = tb.tb_lineno
    #     filename = f.f_code.co_filename
    #     print("An error occurred on line", lineno, "in", filename, ":", error)
    #     print('Unable to create results DataFrame')
        
    #     qna_chain_dict[iteration_id] = simple_summaries_master_list
    # if save_outputs:
    #     try:
    #         save_output(
    #             qna_chain_dict[iteration_id], description='prompt_chain_experiment',
    #             csv_path=csv_path, pickle_path=pickle_path)
    #         save_output(
    #             chaining_bot_dict[iteration_id], description='chaining_bot_dict',
    #             csv_path=None, pickle_path=pickle_path)
    #     except:
    #         print('[prompt_chaining_dict()] Unable to save outputs')
    # return qna_chain_dict
    simple_summaries_dict[iteration_id] = simple_summaries_master_list
    return simple_summaries_dict


iteration_id = 5
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()
simple_summaries_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 3.9
pause_per_request=18
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# simple_summaries_dict = prompt_chaining_dict(simplify_prompts, simple_summaries_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

### qna dict

In [185]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in inactive adults. These snacks involving cycles and stair climbing are efficacious for improving CRF and exercise perf...   
2  Exercise snacks, defined as brief and isolated bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks are efficacious for improving cardiorespiratory fitness and exercise performanc...   
1  Hey! Have you heard about exercise snacks? It's a new concept where you perform isolated bouts of brief vigorous exercise multiple times throughout the day. There's emerging evidence that exercise snacks can improve cardiorespiratory fitness (CRF) and exercise performance in inactive adults. The...   
2  Hey, have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health! Basically, 

In [186]:
simple_summaries_dict = prompt_chaining_dict(simplify_prompts, simple_summaries_dict, chaining_dict[summary_iteration_id], iteration_id,
    n_choices=2, pause_per_request=pause_per_request,
    simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
    )

summary_iteration_id: 5
n_choices: 2
**text1_prompt00
	...Prompt: Assume your audience has no science background., iteration 0
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 18 sec to avoid exceeding API rate limit
		...Preparing to summarize response_02
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 18 sec to avoid exceeding API rate limit
	...Prompt: Make the language appropriate for a lay audience, iteration 1
		...Preparing to summarize response_01
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Summary given
	...Summary given
[.simplify()] Sleeping 18 sec to avoid exceeding API rate limit
		...Preparin

In [190]:
pd.DataFrame(simple_summaries_dict[iteration_id][0])

0  \
simple_summary01_option01  Exercise Snacks is a new approach to improve your cardiovascular and metabolic health. It involves doing short, intense bursts of exercise throughout the day, rather than one long workout. Studies have shown that doing exercise snacks can improve your fitness level and exercise performance, even...   
simple_summary01_option02  Exercise snacks may be a new way to improve our health through brief periods of vigorous exercise performed multiple times throughout the day. These brief workouts involve hard efforts such as cycling or stair climbing and are only 15-30 seconds long. Studies have shown that exercise snacks are ...   
simple_summary02_option01  Exercise snacks are a new and innovative way to improve your health. They involve short bursts of vigorous exercise throughout the day, rather than one long workout. Studies have shown that exercise snacks, which can involve activities like stair climbing or cycling, can help improve your cardio...   
simple_summary02_option02  Exercise Snacks is a new idea that involves short bursts of vigorous exercise throughout the day. The goal is to improve our health by interrupting long periods of sitting and getting our hearts pumping. The research suggests that even small amounts of exercise can make a difference, and that ex...   
simplify task                                                                                                                                                                                                                                                                          Assume your audience has no science background.   

                                                                                                                                                                                                                                                                                                                                     1  
simple_summary01_option01  Exercise Snacks: A Simple Way to Improve Health\n\nDo you often find it hard to make time for exercise? If so, you're not alone. Many people struggle to fit exercise into their busy schedules. Fortunately, a new approach to exercise called "exercise snacks" may be the solution. Exercise snacks a...  
simple_summary01_option02  Exercise snacks are a new approach to improving your health through short bursts of vigorous exercise. These snacks involve performing brief periods of hard effort, such as climbing stairs, multiple times throughout the day. Studies have shown that exercise snacks can improve your cardiorespirat...  
simple_summary02_option01  Exercise snacks are a new and innovative way to improve your heart health and overall fitness. These brief and intense exercise sessions involve performing multiple bouts of vigorous exercise throughout the day. Recent studies have shown that exercise snacks can improve cardiovascular fitness an...  
simple_summary02_option02  Exercise snacks, or brief bursts of vigorous exercise performed multiple times throughout the day, may be an effective way to improve heart health and lower the risk of diseases like type 2 diabetes and heart disease. Studies have shown that even short bouts of intense exercise like climbing sta...  
simplify task                                                                                                                                                                                                                                                                         Make the language appropriate for a lay audience

In [194]:
pd.DataFrame(simple_summaries_dict[iteration_id][-1])

0  \
simple_summary01_option01  This study looked at how seeing pictures of tasty food and feeling stressed affects how much people eat. The researchers found that seeing pictures of tasty food and feeling stressed both increased people's cravings for junk food, and that this led to people eating more junk food. They also foun...   
simple_summary01_option02  This study looked at how seeing pictures of tasty food and feeling stressed affects how much people snack on unhealthy foods. The researchers found that both seeing pictures of tasty food and feeling stressed can make people crave and eat more unhealthy foods. They also found that hormones in ou...   
simple_summary02_option01  This study looked at how seeing pictures of tasty foods and feeling stressed affects how much people snack on unhealthy foods. The researchers found that both seeing the pictures and feeling stressed made people crave and eat more unhealthy snacks. They also found that certain hormones in our bo...   
simple_summary02_option02  This study looked at how seeing pictures of delicious snacks and feeling stressed affects people's cravings for those snacks and how much they actually eat. The researchers found that both seeing the pictures and feeling stressed made people crave the snacks more and eat more of them. They also ...   
simplify task                                                                                                                                                                                                                                                                          Assume your audience has no science background.   

                                                                                                                                                                                                                                                                                                                                     1  
simple_summary01_option01  This study looked at how seeing pictures of delicious snacks and feeling stressed affects our desire to eat those snacks. The researchers found that both food cues and stress make us want to eat more of these snacks, and people who are overweight may be more affected by stress than those who are...  
simple_summary01_option02  This study looked at how food cues and stress affect our desire to eat highly palatable (HP) foods, and whether hormones play a role in this process. The study involved healthy adults who were exposed to either food cues or stress, and then given the opportunity to snack on HP foods. Results sho...  
simple_summary02_option01  This study looked at how exposure to pictures of tasty foods and stress affects people's cravings for and intake of unhealthy snacks. The researchers found that both food cues and stress increased cravings for these snacks, and people who experienced both were more likely to snack on unhealthy f...  
simple_summary02_option02  This study looked at how seeing pictures of tasty snacks or feeling stressed affects our desire to eat those snacks. The study was done in a hospital with healthy adults. The researchers found that both seeing pictures of tasty snacks and feeling stressed increased the desire to eat those snacks...  
simplify task                                                                                                                                                                                                                                                                         Make the language appropriate for a lay audience

### simple_summaries_dict

In [209]:
simple_summaries_dict[iteration_id][0] == simple_summaries_dict[iteration_id][1]

True

In [193]:
print(len(simple_summaries_dict[iteration_id]))
simple_summaries_dict[iteration_id]

8


[{0: {'simple_summary01_option01': "Exercise Snacks is a new approach to improve your cardiovascular and metabolic health. It involves doing short, intense bursts of exercise throughout the day, rather than one long workout. Studies have shown that doing exercise snacks can improve your fitness level and exercise performance, even if you are currently inactive. The exercises can be as simple as climbing stairs or doing jumping jacks, and can be done at home, work, or school. Exercise snacks can also help to reduce the negative effects of sitting for long periods of time and can potentially improve vascular health. Overall, exercise snacks are a simple and feasible way to improve your health and fitness, even if you don't have a lot of time to dedicate to exercise.",
   'simple_summary01_option02': 'Exercise snacks may be a new way to improve our health through brief periods of vigorous exercise performed multiple times throughout the day. These brief workouts involve hard efforts such 

In [189]:
chatbot_dict[summary_iteration_id]['text1_prompt00'].simple_summary_dict

{0: {'simple_summary01_option01': "Exercise Snacks is a new approach to improve your cardiovascular and metabolic health. It involves doing short, intense bursts of exercise throughout the day, rather than one long workout. Studies have shown that doing exercise snacks can improve your fitness level and exercise performance, even if you are currently inactive. The exercises can be as simple as climbing stairs or doing jumping jacks, and can be done at home, work, or school. Exercise snacks can also help to reduce the negative effects of sitting for long periods of time and can potentially improve vascular health. Overall, exercise snacks are a simple and feasible way to improve your health and fitness, even if you don't have a lot of time to dedicate to exercise.",
  'simple_summary01_option02': 'Exercise snacks may be a new way to improve our health through brief periods of vigorous exercise performed multiple times throughout the day. These brief workouts involve hard efforts such as

In [195]:
pd.DataFrame(chatbot_dict[summary_iteration_id]['text1_prompt00'].simple_summary_dict)

0  \
simple_summary01_option01  Exercise Snacks is a new approach to improve your cardiovascular and metabolic health. It involves doing short, intense bursts of exercise throughout the day, rather than one long workout. Studies have shown that doing exercise snacks can improve your fitness level and exercise performance, even...   
simple_summary01_option02  Exercise snacks may be a new way to improve our health through brief periods of vigorous exercise performed multiple times throughout the day. These brief workouts involve hard efforts such as cycling or stair climbing and are only 15-30 seconds long. Studies have shown that exercise snacks are ...   
simple_summary02_option01  Exercise snacks are a new and innovative way to improve your health. They involve short bursts of vigorous exercise throughout the day, rather than one long workout. Studies have shown that exercise snacks, which can involve activities like stair climbing or cycling, can help improve your cardio...   
simple_summary02_option02  Exercise Snacks is a new idea that involves short bursts of vigorous exercise throughout the day. The goal is to improve our health by interrupting long periods of sitting and getting our hearts pumping. The research suggests that even small amounts of exercise can make a difference, and that ex...   
simplify task                                                                                                                                                                                                                                                                          Assume your audience has no science background.   

                                                                                                                                                                                                                                                                                                                                     1  
simple_summary01_option01  Exercise Snacks: A Simple Way to Improve Health\n\nDo you often find it hard to make time for exercise? If so, you're not alone. Many people struggle to fit exercise into their busy schedules. Fortunately, a new approach to exercise called "exercise snacks" may be the solution. Exercise snacks a...  
simple_summary01_option02  Exercise snacks are a new approach to improving your health through short bursts of vigorous exercise. These snacks involve performing brief periods of hard effort, such as climbing stairs, multiple times throughout the day. Studies have shown that exercise snacks can improve your cardiorespirat...  
simple_summary02_option01  Exercise snacks are a new and innovative way to improve your heart health and overall fitness. These brief and intense exercise sessions involve performing multiple bouts of vigorous exercise throughout the day. Recent studies have shown that exercise snacks can improve cardiovascular fitness an...  
simple_summary02_option02  Exercise snacks, or brief bursts of vigorous exercise performed multiple times throughout the day, may be an effective way to improve heart health and lower the risk of diseases like type 2 diabetes and heart disease. Studies have shown that even short bouts of intense exercise like climbing sta...  
simplify task                                                                                                                                                                                                                                                                         Make the language appropriate for a lay audience

### Example

In [217]:
print(pd.concat([pd.DataFrame(value) for value in simple_summaries_dict[iteration_id]]).shape)
print(pd.concat([pd.DataFrame(chatbot_dict[summary_iteration_id][key].simple_summary_dict) for key in chatbot_dict[summary_iteration_id].keys()]).shape)
print(pd.concat([pd.DataFrame(chatbot_dict[summary_iteration_id][key].simple_summary_dict) for key in chatbot_dict[summary_iteration_id].keys()]).transpose().columns)
pd.concat([pd.DataFrame(chatbot_dict[summary_iteration_id][key].simple_summary_dict) for key in chatbot_dict[summary_iteration_id].keys()]).transpose()

(40, 2)
(20, 2)
Index(['simple_summary01_option01', 'simple_summary01_option02',
       'simple_summary02_option01', 'simple_summary02_option02',
       'simplify task', 'simple_summary01_option01',
       'simple_summary01_option02', 'simple_summary02_option01',
       'simple_summary02_option02', 'simplify task',
       'simple_summary01_option01', 'simple_summary01_option02',
       'simple_summary02_option01', 'simple_summary02_option02',
       'simplify task', 'simple_summary01_option01',
       'simple_summary01_option02', 'simple_summary02_option01',
       'simple_summary02_option02', 'simplify task'],
      dtype='object')


simple_summary01_option01  \
0  Exercise Snacks is a new approach to improve your cardiovascular and metabolic health. It involves doing short, intense bursts of exercise throughout the day, rather than one long workout. Studies have shown that doing exercise snacks can improve your fitness level and exercise performance, even...   
1  Exercise Snacks: A Simple Way to Improve Health\n\nDo you often find it hard to make time for exercise? If so, you're not alone. Many people struggle to fit exercise into their busy schedules. Fortunately, a new approach to exercise called "exercise snacks" may be the solution. Exercise snacks a...   

                                                                                                                                                                                                                                                                                     simple_summary01_option02  \
0  Exercise snacks may be a new way to improve our health through brief periods of vigorous exercise performed multiple times throughout the day. These brief workouts involve hard efforts such as cycling or stair climbing and are only 15-30 seconds long. Studies have shown that exercise snacks are ...   
1  Exercise snacks are a new approach to improving your health through short bursts of vigorous exercise. These snacks involve performing brief periods of hard effort, such as climbing stairs, multiple times throughout the day. Studies have shown that exercise snacks can improve your cardiorespirat...   

                                                                                                                                                                                                                                                                                     simple_summary02_option01  \
0  Exercise snacks are a new and innovative way to improve your health. They involve short bursts of vigorous exercise throughout the day, rather than one long workout. Studies have shown that exercise snacks, which can involve activities like stair climbing or cycling, can help improve your cardio...   
1  Exercise snacks are a new and innovative way to improve your heart health and overall fitness. These brief and intense exercise sessions involve performing multiple bouts of vigorous exercise throughout the day. Recent studies have shown that exercise snacks can improve cardiovascular fitness an...   

                                                                                                                                                                                                                                                                                     simple_summary02_option02  \
0  Exercise Snacks is a new idea that involves short bursts of vigorous exercise throughout the day. The goal is to improve our health by interrupting long periods of sitting and getting our hearts pumping. The research suggests that even small amounts of exercise can make a difference, and that ex...   
1  Exercise snacks, or brief bursts of vigorous exercise performed multiple times throughout the day, may be an effective way to improve heart health and lower the risk of diseases like type 2 diabetes and heart disease. Studies have shown that even short bouts of intense exercise like climbing sta...   

                                      simplify task  \
0   Assume your audience has no science background.   
1  Make the language appropriate for a lay audience   

                                                                                                                                                                                                                                                                                     simple_summary01_option01  \
0  Exercise snacks are a new and innovative way to improve our health through physical activity. They involve short, intense burs

In [203]:
simple_summaries_dict[iteration_id]

[{0: {'simple_summary01_option01': "Exercise Snacks is a new approach to improve your cardiovascular and metabolic health. It involves doing short, intense bursts of exercise throughout the day, rather than one long workout. Studies have shown that doing exercise snacks can improve your fitness level and exercise performance, even if you are currently inactive. The exercises can be as simple as climbing stairs or doing jumping jacks, and can be done at home, work, or school. Exercise snacks can also help to reduce the negative effects of sitting for long periods of time and can potentially improve vascular health. Overall, exercise snacks are a simple and feasible way to improve your health and fitness, even if you don't have a lot of time to dedicate to exercise.",
   'simple_summary01_option02': 'Exercise snacks may be a new way to improve our health through brief periods of vigorous exercise performed multiple times throughout the day. These brief workouts involve hard efforts such 

In [210]:
save_output(chatbot_dict[iteration_id], description='chaining_bot_dict')
save_output(qna_dict[iteration_id], description='prompt_chain_experiment')

File saved:  C:/Users/silvh/OneDrive/lighthouse/Ginkgo coding/content-summarization/output/pickles/chaining_bot_dict_2023-04-18_1005.sav
Time completed: 2023-04-18 10:05:15.588762
	Object saved as pickle


TypeError: unsupported operand type(s) for &: 'type' and 'bool'

In [213]:
pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
savepickle(qna_dict[iteration_id], filename='prompt_chain_experiment', append_version=True, path=pickle_path)

File saved:  C:/Users/silvh/OneDrive/lighthouse/Ginkgo coding/content-summarization/output/pickles/prompt_chain_experiment2023-04-18_1008.sav
Time completed: 2023-04-18 10:08:01.543791


In [214]:
qna_dict[iteration_id]

article_title  \
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
2                                        Exercise Snacks A Novel Strategy to Improve Cardiometabolic Health   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
1  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   
2  Food craving, cortisol and ghrelin responses in modeling highly palatable snack intake in the laboratory   

                                   system_role          model  \
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   
1  You are an expert at science communication.  gpt-3.5-turbo   
2  You are an expert at science communication.  gpt-3.5-turbo   

                                          prep step  \
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   
1  Take the key points and numerical descriptors to   
2  Take the key points and numerical descriptors to   

                                                     summarization task  \
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   
1                                         Summarize for a LinkedIn post   
2                                         Summarize for a LinkedIn post   
1  Describe the interesting points to your coworker at the water cooler   
2  Describe the interesting points to your coworker at the water cooler   

                                                                                                                                                                                                                                                                                                       summary  \
1  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in inactive adults. These snacks involving cycles and stair climbing are efficacious for improving CRF and exercise perf...   
2  Exercise snacks, defined as brief and isolated bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks are efficacious for improving cardiorespiratory fitness and exercise performanc...   
1  Hey! Have you heard about exercise snacks? It's a new concept where you perform isolated bouts of brief vigorous exercise multiple times throughout the day. There's emerging evidence that exercise snacks can improve cardiorespiratory fitness (CRF) and exercise performance in inactive adults. The...   
2  Hey, have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health! Basically, 

In [227]:
chatbot_dict[iteration_id]['text1_prompt00'].summaries_dict

{'response_01': 'Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in inactive adults. These snacks involving cycles and stair climbing are efficacious for improving CRF and exercise performance. The potential for exercise snacks to improve vascular health and reduce the impact of sedentariness on cardiometabolic health is promising. Exercise snacks align with the revised Physical Activity Guidelines for Americans and the World Health Organization Guidelines on Physical Activity and Sedentary Behavior. The applicability of exercise snacks in a real-world setting and their potential to target musculoskeletal health remain to be determined.',
 'response_02': 'Exercise snacks, defined as brief and isolated bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercis

### 5.1 new function

In [228]:
chatbot_dict[iteration_id].keys()

dict_keys(['text1_prompt00', 'text1_prompt01', 'text2_prompt00', 'text2_prompt01'])

In [221]:
def process_summaries(qna_dict, chatbot_dict, iteration_id):
    """
    Merge the qna_dict and chatbot_dict into a single DataFrame
    """

    # summaries = pd.concat(
    #     [pd.DataFrame(chatbot_dict[iteration_id][key].summaries_dict, index=[0]) for key in chatbot_dict[iteration_id].keys()]
    #     )
    return summaries

process_summaries(qna_dict, chatbot_dict, iteration_id)

response_01  \
0  Exercise snacks, defined as isolated bouts of brief vigorous exercise performed multiple times throughout the day, may be a feasible strategy to improve cardiometabolic health in inactive adults. These snacks involving cycles and stair climbing are efficacious for improving CRF and exercise perf...   
0  Hey! Have you heard about exercise snacks? It's a new concept where you perform isolated bouts of brief vigorous exercise multiple times throughout the day. There's emerging evidence that exercise snacks can improve cardiorespiratory fitness (CRF) and exercise performance in inactive adults. The...   
0  New research compares the effects of food cue and stress exposure on highly palatable food craving and intake. The study found that exposure to both personal food cues and stressors resulted in increases in highly palatable food craving and subsequent increased snacking of these foods. Ghrelin a...   
0  Hey! I just read this interesting study about how exposure to both food cues and stress can increase our cravings for highly palatable foods and lead to snacking on them. The study was conducted within a controlled hospital-based setting with healthy community adults, and it found that food cues...   

                                                                                                                                                                                                                                                                                                   response_02  
0  Exercise snacks, defined as brief and isolated bouts of vigorous exercise performed multiple times throughout the day, may be an effective strategy to improve cardiometabolic health. Studies show that exercise snacks are efficacious for improving cardiorespiratory fitness and exercise performanc...  
0  Hey, have you heard about exercise snacks? It's a new strategy to improve cardiometabolic health! Basically, it involves isolated bouts of brief vigorous exercise performed multiple times throughout the day. And the best part is, it's not time-consuming at all! \n\nStudies have shown that exerci...  
0  New research conducted in a hospital-based setting with healthy adults shows that exposure to both food cues and stress increases highly palatable food cravings and subsequent snacking of these foods. Cortisol and ghrelin hormones appear to play a role in food cue and stress related food motivat...  
0  Hey! I just read an interesting study on food cravings and stress. The study found that exposure to both personal food cues and stressors resulted in increases in highly palatable food cravings and subsequent snacking of those foods. The study also found that ghrelin and cortisol hormones appear...

In [223]:
def process_simple_summaries(qna_dict, chatbot_dict, iteration_id):
    """
    Merge the qna_dict and chatbot_dict into a single DataFrame
    """
    simple_summaries = pd.concat(
        [pd.DataFrame(chatbot_dict[iteration_id][key].simple_summary_dict).transpose() for key in chatbot_dict[iteration_id].keys()]
        )
    return simple_summaries

process_simple_summaries(qna_dict, chatbot_dict, iteration_id)

simple_summary01_option01  \
0  Exercise Snacks is a new approach to improve your cardiovascular and metabolic health. It involves doing short, intense bursts of exercise throughout the day, rather than one long workout. Studies have shown that doing exercise snacks can improve your fitness level and exercise performance, even...   
1  Exercise Snacks: A Simple Way to Improve Health\n\nDo you often find it hard to make time for exercise? If so, you're not alone. Many people struggle to fit exercise into their busy schedules. Fortunately, a new approach to exercise called "exercise snacks" may be the solution. Exercise snacks a...   
0  Exercise snacks are a new and innovative way to improve our health through physical activity. They involve short, intense bursts of exercise performed multiple times throughout the day. Studies have shown that exercise snacks can improve our fitness levels and reduce the harmful effects of sitti...   
1  Exercise Snacks: A Simple Way to Improve Your Health\n\nDo you struggle to find time for exercise in your busy schedule? Do you find it hard to stick to a regular exercise routine? If so, "exercise snacks" may be the solution you've been looking for.\n\nExercise snacks involve short bursts of in...   
0  This study looked at how seeing pictures of delicious food and feeling stressed affects how much people eat of those foods. The researchers found that both seeing pictures of tasty food and feeling stressed made people crave and eat more of those foods. The hormones ghrelin and cortisol also pla...   
1  This study looked at how seeing pictures of tasty food and feeling stressed affects our cravings for unhealthy snacks and how much we eat of them. The researchers found that both of these situations increased our desire for highly palatable foods, and that people who are overweight may be more a...   
0  This study looked at how seeing pictures of tasty food and feeling stressed affects how much people eat. The researchers found that seeing pictures of tasty food and feeling stressed both increased people's cravings for junk food, and that this led to people eating more junk food. They also foun...   
1  This study looked at how seeing pictures of delicious snacks and feeling stressed affects our desire to eat those snacks. The researchers found that both food cues and stress make us want to eat more of these snacks, and people who are overweight may be more affected by stress than those who are...   

                                                                                                                                                                                                                                                                                     simple_summary01_option02  \
0  Exercise snacks may be a new way to improve our health through brief periods of vigorous exercise performed multiple times throughout the day. These brief workouts involve hard efforts such as cycling or stair climbing and are only 15-30 seconds long. Studies have shown that exercise snacks are ...   
1  Exercise snacks are a new approach to improving your health through short bursts of vigorous exercise. These snacks involve performing brief periods of hard effort, such as climbing stairs, multiple times throughout the day. Studies have shown that exercise snacks can improve your cardiorespirat...   
0  Exercise snacks are a new and easy way to improve your health by doing short bouts of vigorous exercise throughout the day. These exercises are very short, lasting only 15-30 seconds and can be done using a cycle or by climbing stairs. They are great for people who are not very active and can he...   
1  Do you struggle to find time for exercise in your busy schedule? Well, there's good news! A recent study suggests that "exercise snacks" - short bursts of vigorous exercise performed several times throughout the day - can be an effective way to improve your cardiorespiratory fitness and overall

# Iteration 6

In [ ]:
import time
class Chaining:
    """
    Requrired paramaters:
        - text (str): Text to feed to GPT for summarization.

    Optional parameters
        - system_role (str): ChatGPT parameter. 
            Default is "You are an expert at science communication."
        - temperature (float): ChatGPT parameter. Default is 0.7.
        - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
        - max_tokens (int): Token limit for ChatGPT response.
        - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
    """

    def __init__(self, text, model="gpt-3.5-turbo", temperature=0.7, max_tokens=1000, 
        system_role = "You are an expert at science communication."):
        self.text = text
        self.system_role = system_role
        self.temperature = temperature
        self.max_tokens = max_tokens
        self.model = model
    
    def create_prompt(self, task):
        system_role = f'{self.system_role}'
        user_input = f"""Given the following text: {self.text} \n {task}"""
        messages = [
        {"role": "system", "content": system_role},
        {"role": "user", "content": user_input},]

        print('\tDone creating prompt')
        return messages

    def gpt(self, messages, n_choices):
        print('\tSending request to GPT-3')
        print(f'\t\tRequesting {n_choices} choices using {self.model}')
        openai.api_key = os.getenv('api_openai')
        response = openai.ChatCompletion.create(
            model=self.model, messages=messages, 
            temperature=self.temperature, 
            max_tokens=self.max_tokens,
            n=n_choices
            )
        print('\tDone sending request to GPT-3')
        return response

    def summarize(self, task, prep_step=None, n_choices=5
        ):
        """
        SH 2023-04-11 12:18: Same as the user-defined `reply` function, but re-written as a class method.
        Send a ChatCompletion request to ChatGPT via the Chaining class.

        Requrired paramaters:
            - task (str): Task to include in ChatGPT prompt.
            - text (str): Text to feed to GPT for summarization.

        Optional parameters
            - system_role (str): ChatGPT parameter. 
                Default is "You are an expert at science communication."
            - temperature (float): ChatGPT parameter. Default is 0.7.
            - n_choices (int): Number of ChatGPT responses to generate. Default is 5.
            - max_tokens (int): Token limit for ChatGPT response.
            - model (str): ChatGPT model to use. Default is "gpt-3.5-turbo".
        """
        chatbot = Chaining(self.text)
        prompt = chatbot.create_prompt(task)
        firstline_pattern = r'\s?(\S*)(\n*)(.+)'
        title = re.match(firstline_pattern, self.text)[0]
        self.qna = dict() 
        self.qna['article_title'] = title
        self.qna['system_role'] = self.system_role
        self.qna['model'] = self.model
        self.qna['prep step'] = prep_step
        self.qna['summarization task'] = task
        self.summaries_dict = dict()
        self.article_title = title
        self.response_regex = r'response_(.*)'
        self.simple_summary_dict = dict()

        try:
            response = chatbot.gpt(prompt, n_choices=n_choices)
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**API request failed for `.summarize()`**')
            return self.qna
        try:
            for index, choice in enumerate(response.choices):
                self.summaries_dict[f'response_{"{:02d}".format(index+1)}'] = choice["message"]["content"]
            self.qna.setdefault('summary', [])
            self.qna['summary'].extend([value for value in self.summaries_dict.values()])
            self.qna[f'text'] = self.text
            return self.qna
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('\t**Error with response parsing**')
            return self.qna


    def simplify(self, simplify_task, system_role='You are an expert at science communication.',
                    model="gpt-3.5-turbo", temperature=0.0, n_choices=1, max_tokens=1000, 
                    simplify_iteration=None, pause_per_request=20
                    ):
        self.simple_summary_dict[simplify_iteration] = dict()
        if simplify_iteration == None:
            simplify_iteration = 1
        for key in self.summaries_dict.keys():
            new_key = re.sub(self.response_regex, rf'simple_summary\1', key)
            print(f'\t\t...Preparing to summarize {key}')
            simplify_prompt = self.create_prompt(simplify_task)
            try:
                response = self.gpt(simplify_prompt, n_choices)
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t**API request failed for `.simplify()`**')
                return self.qna
            try:
                for index, choice in enumerate(response.choices):
                    simple_summary_option = f'{new_key}_option{"{:02d}".format(index+1)}'
                    self.simple_summary_dict[simplify_iteration].setdefault(simple_summary_option, {})
                    self.simple_summary_dict[simplify_iteration][simple_summary_option] = choice["message"]["content"]                    
                    print(f'\t...Summary given')
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                self.simple_summary_dict[simplify_iteration][new_key] = response
                print(f'\t...Error parsing response for summary request')
            print(f'[.simplify()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
            time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
        self.simple_summary_dict[simplify_iteration]['summary'] = self.summaries_dict
        self.simple_summary_dict[simplify_iteration]['simplify task'] = simplify_task
        return self.simple_summary_dict


def batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chaining_bot_dict, iteration_id, n_choices=5,
    prompt_column='prompt', pause_per_request=20,
    save_outputs=False, filename=None, append_version=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Summarize multiple texts using the same prompts.
    Parameters:
        - prep_step, summarize_task (list)
        - qna_dict: Dictionary to store the input and outputs.
        - iteration_id (int, float, or string): Unique ID serving as the key for results in the qna_dict
        - prompt_column (str): Name of the column in the prompts_df containing the user input.

    """
    temp_qna_dict = dict()
    qna_dfs_list = []
    prompts_df = pd.DataFrame(product(prep_step, summarize_task), 
        columns=['prep_step', 'summarize_task'])

    chaining_bot_dict[iteration_id] = dict()
    for key in text_dict:
        text = text_dict[key]
        temp_qna_dict[key] = dict()
        for index in prompts_df.index:
            print(f'**Text #{key} prompt #{index} of {prompts_df.index.max()}**')
            task = prompts_df.loc[index, 'summarize_task']
            prep_step = prompts_df.loc[index, 'prep_step']
            try:
                print('Creating Chaining class instance')
                chatbot = Chaining(text)
                print('Chaining class instance created')
                temp_qna_dict[key][index] = chatbot.summarize(task=task, prep_step=prep_step, n_choices=n_choices)
                chaining_bot_dict[iteration_id][f'text{key}_prompt{"{:02d}".format(index)}'] = chatbot
                print('\t...Success!')
                print(f'[batch_summarize()] Sleeping {pause_per_request} sec to avoid exceeding API rate limit')
                time.sleep(pause_per_request) # Account for API rate limit of 3 API requests/limit 
            except Exception as error:
                exc_type, exc_obj, tb = sys.exc_info()
                f = tb.tb_frame
                lineno = tb.tb_lineno
                filename = f.f_code.co_filename
                print("An error occurred on line", lineno, "in", filename, ":", error)
                print('\t...Error making chatbot request')
                break
        
        try:
            updated_qna_dict = (temp_qna_dict[key])
        except Exception as error:
            exc_type, exc_obj, tb = sys.exc_info()
            f = tb.tb_frame
            lineno = tb.tb_lineno
            filename = f.f_code.co_filename
            print("An error occurred on line", lineno, "in", filename, ":", error)
            print('Error concatenating prompts DataFrame')
            return temp_qna_dict, chaining_bot_dict
        qna_dfs_list.append(updated_qna_dict)
    try:
        qna_dict[iteration_id] = pd.concat([
            pd.DataFrame(
                data, index=[choice for choice in range(1, len(data['summary'])+1)]
            ) for dictionary in qna_dfs_list for data in dictionary.values()
        ])
        if save_outputs:
            try:
                save_output(
                    qna_dict[iteration_id], description='prompt_chain_experiment',
                    csv_path=csv_path, pickle_path=pickle_path)
                save_output(
                    chaining_bot_dict[iteration_id], description='chaining_bot_dict',
                    csv_path=None, pickle_path=pickle_path)
            except:
                print('[prompt_chaining_dict()] Unable to save outputs')
    except Exception as error:
        exc_type, exc_obj, tb = sys.exc_info()
        f = tb.tb_frame
        lineno = tb.tb_lineno
        filename = f.f_code.co_filename
        print("An error occurred on line", lineno, "in", filename, ":", error)
        qna_dict[iteration_id] = qna_dfs_list
        print('Error creating DataFrame; dictionary returned instead')
    return qna_dict, chaining_bot_dict

def prompt_chaining_dict(simplify_prompts, simple_summaries_dict, chaining_bot_dict, iteration_id,
    summary_iteration_id=None, n_choices=None, pause_per_request=20,
    prompt_column='simplify', simplify_iteration=None, save_outputs=False,
    csv_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output',
    pickle_path=r'C:\Users\silvh\OneDrive\lighthouse\Ginkgo coding\content-summarization\output\pickles'
    ):
    """
    Simplify or add context to a summary.
    """
    summary_iteration_id = summary_iteration_id if summary_iteration_id else iteration_id
    print('summary_iteration_id:', summary_iteration_id)
    if n_choices == None:
        n_choices = 1 if prompt_column == 'simplify' else 5
    print('n_choices:', n_choices)
    if type(simplify_prompts) == str:
        simplify_prompts = [simplify_prompts]
    elif type(simplify_prompts) == pd.core.frame.DataFrame:
        simplify_prompts = [prompt for prompt in simplify_prompts[prompt_column].unique() if len(prompt) >1]
    else:
        simplify_prompts = list(set([prompt for prompt in simplify_prompts if len(prompt) >1]))
    simple_summaries_master_list = []
    for text_prompt_key in chaining_bot_dict.keys():
        print(f'**{text_prompt_key}')
        # simple_summaries_master_dict[text_prompt_key] = dict()

        for index, prompt in enumerate(simplify_prompts):
            relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
            print(f'\t...Prompt: {prompt}, iteration {relevance_iteration}')
            if prompt_column == 'simplify':
                summary_dict = chaining_bot_dict[text_prompt_key].simplify(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    simplify_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            else: 
                summary_dict = chaining_bot_dict[text_prompt_key].add_relevance(
                    prompt, n_choices=n_choices, pause_per_request=pause_per_request, 
                    relevance_iteration=index if len(simplify_prompts) > 1 else simplify_iteration
                    )
            simple_summaries_master_list.append(summary_dict)
  
    simple_summaries_dict[iteration_id] = simple_summaries_master_list
    return simple_summaries_dict


iteration_id = 5
n_choices = 2
# qna_dict = dict()
# chatbot_dict = dict()
simple_summaries_dict = dict()

summarize_task = task_part1
simplify_prompts = task_part2

summary_iteration_id = iteration_id
# summary_iteration_id = 3.9
pause_per_request=0
# relevance_prompts = relevance_prompts_df

qna_dict, chaining_dict = batch_summarize_chain(text_dict, prep_step, summarize_task, qna_dict, chatbot_dict, 
    n_choices=n_choices, pause_per_request=pause_per_request,
    iteration_id=iteration_id)

# simple_summaries_dict = prompt_chaining_dict(simplify_prompts, simple_summaries_dict, chaining_dict[summary_iteration_id], iteration_id,
#     n_choices=2, pause_per_request=pause_per_request,
#     simplify_iteration=1, summary_iteration_id=summary_iteration_id, save_outputs=False
#     )

**Text #1 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #1 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #2 prompt #0 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating prompt
	Sending request to GPT-3
		Requesting 2 choices using gpt-3.5-turbo
	Done sending request to GPT-3
	...Success!
[batch_summarize()] Sleeping 18 sec to avoid exceeding API rate limit
**Text #2 prompt #1 of 1**
Creating Chaining class instance
Chaining class instance created
	Done creating pr

# *End of Page*